In [1]:
# Threading and determinism guards (per audit recommendation)
import os
os.environ['OMP_NUM_THREADS'] = '1'
os.environ['OPENBLAS_NUM_THREADS'] = '1'
os.environ['MKL_NUM_THREADS'] = '1'
os.environ['VECLIB_MAXIMUM_THREADS'] = '1'
os.environ['NUMEXPR_NUM_THREADS'] = '1'
os.environ['CUDA_DEVICE_ORDER'] = 'PCI_BUS_ID'
os.environ['TOKENIZERS_PARALLELISM'] = 'false'
# Enforce cuBLAS determinism (must be set before importing torch)
os.environ['CUBLAS_WORKSPACE_CONFIG'] = ':4096:8'
# Mitigate CUDA fragmentation per audit
os.environ['PYTORCH_CUDA_ALLOC_CONF'] = 'expandable_segments:True,max_split_size_mb:128'

try:
    import torch
    torch.set_num_threads(1)
    torch.set_num_interop_threads(1)
    # Enable TF32 for speed/stability on Ampere+
    try:
        torch.backends.cuda.matmul.allow_tf32 = True
        torch.backends.cudnn.allow_tf32 = True
    except Exception:
        pass
except Exception:
    pass

try:
    import cv2
    try:
        cv2.setNumThreads(0)
    except Exception:
        pass
    try:
        cv2.ocl.setUseOpenCL(False)
    except Exception:
        pass
except Exception:
    pass

print('Thread limits set. Proceeding...')

Thread limits set. Proceeding...


# APTOS 2019 Blindness Detection — Medal Plan & Experiment Log (Rev A)

Non‑negotiable goal: WIN A MEDAL (optimize Quadratic Weighted Kappa).

## Problem framing
- Task: 5-class ordinal classification (diagnosis ∈ {0,1,2,3,4}) from retinal fundus images.
- Metric: Quadratic Weighted Kappa (QWK) — all early stopping and model selection by val QWK (not loss).
- Submission: submission.csv with columns [id_code, diagnosis].

## Success gates
- First OOF CV + submission within first hour.
- Targets: OOF QWK ≥ 0.914 (bronze), ≥ 0.920 (silver), ≥ 0.930 (gold contention).

## Validation protocol & reproducibility
- 5-fold StratifiedKFold (n_splits=5, shuffle=True, random_state=42). Save fold indices to disk for reuse.
- Fix seeds (Python/NumPy/PyTorch/cudnn). Deterministic where possible.
- Evaluate per-epoch on val:
  - Compute predictions → optimize 4 thresholds on-the-fly (monotonic) → compute QWK.
  - Early stopping/checkpoint on best val QWK.
- After training, aggregate OOF predictions and re-optimize global thresholds (scipy.optimize, constrained increasing cutpoints).

## Data & preprocessing
- EDA: label distribution, image dimension stats, blur/artefact detection (Laplacian variance), count/visualize outliers. Decide keep/filter.
- Retina-specific preprocessing (baseline, mandatory):
  - Ben Graham style circle crop (remove black borders), mask background.
  - Contrast enhancement: CLAHE or color constancy; optional mild unsharp mask.
  - Normalize per-image; keep color information.

## Baseline model (v1)
- Backbone: timm efficientnet_b3 (or b0 if speed constrained) pretrained.
- Input size: 512 px (square, after retina crop; center/pad as needed).
- Head A (Regression): 1-dim regression with SmoothL1; predictions → thresholds → classes.
- Loss: SmoothL1; Optimizer: AdamW (lr=3e-4), weight_decay=1e-4.
- Scheduler: cosine decay with warmup (1 epoch warmup), epochs: 15–20 with early stopping.
- AMP mixed precision; gradient clipping (norm=1.0).
- Batch size: tune for GPU (start 32 @ 512 if memory fits; else 16/24).
- Imbalance handling: class-weighted sampling (WeightedRandomSampler) and/or class-weighted loss (for classification/ordinal variants). Start with sampler.
- Augmentations (conservative for DR): horizontal/vertical flip, small rotate (±10°), RandomResizedCrop/center, brightness/contrast (±0.2), slight Gaussian blur (p small).

## Parallel model (v2 Ordinal)
- Ordinal head: CORN/CORAL (4 binary logits for y>k).
- Loss: BCEWithLogits with class/level weights or focal variant.
- Same preprocessing, CV, and hyperparams. Produces complementary errors for ensembling.

## Threshold optimization
- Optimize 4 cutpoints t0<t1<t2<t3 on OOF predictions to maximize QWK.
- Use scipy.optimize.minimize (e.g., Nelder–Mead/L-BFGS-B) with monotonic constraints; initialize from quantiles.
- Apply global thresholds to fold/test predictions; re-tune per-model if necessary.

## External data (2015 DR)
- Integrate Kaggle DR 2015 dataset:
  - Download and preprocess with same retina pipeline.
  - Strategy: pretrain on external (5 classes mapped consistently), then fine-tune on APTOS; or co-train with sample weighting.
- Track CV impact; proceed only if OOF improves.

## Ensembling, TTA, seeds
- Train across multiple CV seeds: 3 seeds × 5 folds = 15 models per head/backbone.
- Backbones to consider after baseline: efficientnet_b4/b5, convnext_tiny.
- TTA: 4–8 transforms (flips/rotations). Average predictions/logits before thresholding.
- Ensemble diverse models (backbones, heads, seeds, resolutions). Weight by OOF QWK.

## Hyperparameters (initial defaults)
- Optimizer: AdamW(lr=3e-4, wd=1e-4), warmup epochs=1, total epochs=15–20.
- Scheduler: CosineAnnealingLR (or OneCycle as alt ablation).
- Dropout in head: 0.3.
- Early stop patience: 3–5 epochs on val QWK.

## Experiment log
| Exp | Date | Model | Size | Loss | Augs | Sampler | Folds×Seeds | OOF QWK | Notes |
|-----|------|-------|------|------|------|---------|-------------|---------|-------|
| 001 | TBD  | EffNet-B3 reg | 512 | SmoothL1 | retina+light | WRS | 5×1 | TBD | Baseline + thresholds |
| 002 | TBD  | EffNet-B3 CORN | 512 | BCEWL | retina+light | WRS | 5×1 | TBD | Ordinal variant |

## Checkpoints
- [ ] Plan (this cell) → Audit
- [ ] Environment setup (GPU, installs, seeds) → Audit
- [ ] Data load, EDA, retina preprocessing preview → Audit
- [ ] Baseline training (5-fold) with per-epoch val QWK + thresholds → Audit
- [ ] OOF threshold optimization + first submission → Audit
- [ ] Ordinal model + small ensemble + TTA → Audit

## Next actions
1) Env check (GPU), install torch/timm/albumentations/opencv/scipy, set all seeds; create paths.
2) Load CSVs, compute label stats; preview few images before/after retina crop + CLAHE.
3) Implement Dataset/Dataloader with retina pipeline, WeightedRandomSampler, 512 size.
4) Implement training loop: per-epoch val predictions → threshold opt → QWK for early stop/checkpoint.
5) Run 5-fold baseline (seed=42), produce OOF, optimize global thresholds, infer test, save submission.
6) Spin up CORN ordinal variant using same splits; compare OOF; plan ensemble.

We will keep the notebook concise: document here, delete stale code cells after logging results.

In [3]:
import cv2
from tqdm import tqdm

# Mandatory preprocessing specs
CLAHE_CLIP = 2.0
CLAHE_TILE = (8, 8)
TARGET_SIZE = IMG_SIZE  # from globals (Cell 6)
# Dynamic cache size: +32 over crop size (e.g., 256 -> 288, 384 -> 416)
CACHE_SIZE = int(TARGET_SIZE) + 32

# Use cache dirs defined in globals (Cell 6): CACHE_TRAIN_DIR, CACHE_TEST_DIR
os.makedirs(CACHE_TRAIN_DIR, exist_ok=True)
os.makedirs(CACHE_TEST_DIR, exist_ok=True)

def _find_retina_crop(img_bgr, invert: bool = False):
    h, w = img_bgr.shape[:2]
    gray = cv2.cvtColor(img_bgr, cv2.COLOR_BGR2GRAY)
    gray = cv2.medianBlur(gray, 5)  # safer than 11 per audit
    thresh_type = cv2.THRESH_BINARY_INV if invert else cv2.THRESH_BINARY
    _, th = cv2.threshold(gray, 0, 255, thresh_type + cv2.THRESH_OTSU)
    cnts, _ = cv2.findContours(th, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not cnts:
        return None  # signal failure
    cnt = max(cnts, key=cv2.contourArea)
    area_ratio = cv2.contourArea(cnt) / float(h * w + 1e-6)
    (cx, cy), r = cv2.minEnclosingCircle(cnt)
    cx, cy, r = int(cx), int(cy), int(r)
    # bounds of square around circle
    x1, y1 = max(0, cx - r), max(0, cy - r)
    x2, y2 = min(w, cx + r), min(h, cy + r)
    return (cx, cy, r, x1, y1, x2, y2, area_ratio)

def circle_crop_bgr(img_bgr):
    h, w = img_bgr.shape[:2]
    # First attempt normal Otsu
    res = _find_retina_crop(img_bgr, invert=False)
    # Fallback if mask area too small/large
    if res is None or res[7] < 0.20 or res[7] > 0.95:
        res = _find_retina_crop(img_bgr, invert=True)
    # Final fallback: centered square crop if still failing
    if res is None:
        side = min(h, w)
        y1 = (h - side) // 2; x1 = (w - side) // 2
        return img_bgr[y1:y1+side, x1:x1+side]
    cx, cy, r, x1, y1, x2, y2, _ = res
    crop = img_bgr[y1:y2, x1:x2]
    # Mask to circle with correct local coordinates
    ch, cw = crop.shape[:2]
    mask = np.zeros((ch, cw), dtype=np.uint8)
    center_x = cx - x1
    center_y = cy - y1
    rad = min(r, ch // 2, cw // 2)
    cv2.circle(mask, (int(center_x), int(center_y)), int(rad), 255, -1)
    bg = np.zeros_like(crop)
    crop = np.where(mask[..., None] == 255, crop, bg)
    return crop

def apply_clahe_bgr(img_bgr):
    lab = cv2.cvtColor(img_bgr, cv2.COLOR_BGR2LAB)
    L, A, B = cv2.split(lab)
    clahe = cv2.createCLAHE(clipLimit=CLAHE_CLIP, tileGridSize=CLAHE_TILE)
    L2 = clahe.apply(L)
    lab2 = cv2.merge([L2, A, B])
    return cv2.cvtColor(lab2, cv2.COLOR_LAB2BGR)

def resize_preserve_ar_pad_square(img_bgr, target):
    h, w = img_bgr.shape[:2]
    if h == 0 or w == 0:
        return np.zeros((target, target, 3), dtype=np.uint8)
    scale = target / max(h, w)
    nh, nw = int(round(h * scale)), int(round(w * scale))
    resized = cv2.resize(img_bgr, (nw, nh), interpolation=cv2.INTER_AREA)
    top = (target - nh) // 2
    bottom = target - nh - top
    left = (target - nw) // 2
    right = target - nw - left
    padded = cv2.copyMakeBorder(resized, top, bottom, left, right, cv2.BORDER_CONSTANT, value=(0,0,0))
    return padded

def preprocess_and_cache_one(img_path: Path, out_path: Path, cache_size: int = CACHE_SIZE):
    if out_path.exists():
        return
    img = cv2.imread(str(img_path), cv2.IMREAD_COLOR)
    if img is None:
        return
    img = circle_crop_bgr(img)
    img = apply_clahe_bgr(img)
    img = resize_preserve_ar_pad_square(img, cache_size)
    cv2.imwrite(str(out_path), img, [cv2.IMWRITE_PNG_COMPRESSION, 3])

def build_cache(split: str = 'train', limit: int | None = None):
    if split == 'train':
        df = pd.read_csv(FOLDS_CSV) if FOLDS_CSV.exists() else pd.read_csv(TRAIN_CSV)
        out_dir = CACHE_TRAIN_DIR
        ids = df['id_code'].tolist()
        img_dir = TRAIN_IMG_DIR
    else:
        df = pd.read_csv(TEST_CSV)
        out_dir = CACHE_TEST_DIR
        ids = df['id_code'].tolist()
        img_dir = TEST_IMG_DIR
    if limit is not None:
        ids = ids[:limit]
    for idc in tqdm(ids, desc=f'Caching {split} images'):
        in_path = img_dir / f'{idc}.png'
        out_path = out_dir / f'{idc}.png'
        preprocess_and_cache_one(in_path, out_path, CACHE_SIZE)

print('Preprocessing utilities ready. To build cache:')
print('- build_cache("train") and build_cache("test")  [this may take a few minutes].')
print('Cached size =', CACHE_SIZE, '; downstream aug will Crop to', TARGET_SIZE)

Preprocessing utilities ready. To build cache:
- build_cache("train") and build_cache("test")  [this may take a few minutes].
Cached size = 288 ; downstream aug will Crop to 256


In [ ]:
%%time
# Build cached, retina-preprocessed datasets (may take several minutes)
build_cache('train')
build_cache('test')

train_cached = len(list((CACHE_TRAIN_DIR).glob('*.png')))
test_cached = len(list((CACHE_TEST_DIR).glob('*.png')))
print('Cached train images:', train_cached)
print('Cached test images:', test_cached)

In [4]:
import math
from typing import List, Optional, Callable
from pathlib import Path
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader, WeightedRandomSampler
import cv2
import numpy as np
import pandas as pd
import urllib.error

# ---------- QWK (no sklearn) ----------
def qwk_score(y_true: np.ndarray, y_pred: np.ndarray, n_classes: int = 5) -> float:
    y_true = y_true.astype(int).ravel()
    y_pred = y_pred.astype(int).ravel()
    O = np.zeros((n_classes, n_classes), dtype=np.float64)
    for t, p in zip(y_true, y_pred):
        if 0 <= t < n_classes and 0 <= p < n_classes:
            O[t, p] += 1
    N = O.sum()
    if N == 0:
        return 0.0
    hist_true = O.sum(axis=1)
    hist_pred = O.sum(axis=0)
    E = np.outer(hist_true, hist_pred) / (N + 1e-12)
    W = np.zeros((n_classes, n_classes), dtype=np.float64)
    for i in range(n_classes):
        for j in range(n_classes):
            W[i, j] = ((i - j) ** 2) / ((n_classes - 1) ** 2)
    num = (W * O).sum()
    den = (W * E).sum() + 1e-12
    return 1.0 - num / den

# ---------- Thresholding utilities (no scipy) ----------
def preds_to_labels_reg(preds: np.ndarray, th: List[float]) -> np.ndarray:
    t0, t1, t2, t3 = th
    return np.digitize(preds, bins=[t0, t1, t2, t3]).astype(int)

def _enforce_monotonic(th):
    th = list(th)
    th[1] = max(th[1], th[0] + 1e-3)
    th[2] = max(th[2], th[1] + 1e-3)
    th[3] = max(th[3], th[2] + 1e-3)
    return th

def optimize_thresholds(preds: np.ndarray, y_true: np.ndarray, init: Optional[List[float]] = None, n_iter: int = 6) -> List[float]:
    preds = preds.reshape(-1)
    y_true = y_true.reshape(-1)
    if init is None:
        init = list(np.quantile(preds, [0.2, 0.4, 0.6, 0.8]))
    th = _enforce_monotonic(init)
    base_std = preds.std() + 1e-6
    delta = base_std * 0.5
    best = qwk_score(y_true, preds_to_labels_reg(preds, th))
    for _ in range(n_iter):
        improved = False
        for k in range(4):
            for s in (+1, -1):
                cand = th.copy()
                cand[k] += s * delta
                cand = _enforce_monotonic(cand)
                q = qwk_score(y_true, preds_to_labels_reg(preds, cand))
                if q > best + 1e-6:
                    th, best, improved = cand, q, True
        delta *= 0.5
        if not improved:
            continue
    return th

# ---------- Lightweight transforms (no albumentations) ----------
class Compose:
    def __init__(self, tfms: List[Callable]):
        self.tfms = tfms
    def __call__(self, img: np.ndarray) -> np.ndarray:
        for t in self.tfms:
            img = t(img)
        return img

class RandomCrop:
    def __init__(self, h: int, w: int):
        self.h, self.w = h, w
    def __call__(self, img):
        H, W = img.shape[:2]
        if H == self.h and W == self.w:
            return img
        if H < self.h or W < self.w:
            top = max(0, (H - self.h) // 2)
            left = max(0, (W - self.w) // 2)
            bottom = min(H, top + self.h)
            right = min(W, left + self.w)
            canvas = np.zeros((self.h, self.w, 3), dtype=img.dtype)
            patch = img[top:bottom, left:right]
            canvas[0:bottom-top, 0:right-left] = patch
            return canvas
        top = np.random.randint(0, H - self.h + 1)
        left = np.random.randint(0, W - self.w + 1)
        return img[top:top+self.h, left:left+self.w]

class CenterCrop:
    def __init__(self, h: int, w: int):
        self.h, self.w = h, w
    def __call__(self, img):
        H, W = img.shape[:2]
        top = max(0, (H - self.h) // 2)
        left = max(0, (W - self.w) // 2)
        bottom = min(H, top + self.h)
        right = min(W, left + self.w)
        canvas = np.zeros((self.h, self.w, 3), dtype=img.dtype)
        patch = img[top:bottom, left:right]
        canvas[0:bottom-top, 0:right-left] = patch
        return canvas

class HorizontalFlip:
    def __init__(self, p: float = 0.5):
        self.p = p
    def __call__(self, img):
        if np.random.rand() < self.p:
            return cv2.flip(img, 1)
        return img

class VerticalFlip:
    def __init__(self, p: float = 0.5):
        self.p = p
    def __call__(self, img):
        if np.random.rand() < self.p:
            return cv2.flip(img, 0)
        return img

class Rotate:
    def __init__(self, limit: int = 10, p: float = 0.5, border_mode=cv2.BORDER_CONSTANT, value=0):
        self.limit, self.p = limit, p
        self.border_mode, self.value = border_mode, value
    def __call__(self, img):
        if np.random.rand() >= self.p:
            return img
        angle = np.random.uniform(-self.limit, self.limit)
        h, w = img.shape[:2]
        M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1.0)
        return cv2.warpAffine(img, M, (w, h), flags=cv2.INTER_LINEAR, borderMode=self.border_mode, borderValue=self.value)

class GaussianBlurTfm:
    def __init__(self, ksize: int = 3, sigma: float = 0.0, p: float = 0.25):
        self.ksize = ksize if ksize % 2 == 1 else 3
        self.sigma = sigma
        self.p = p
    def __call__(self, img):
        if np.random.rand() >= self.p:
            return img
        return cv2.GaussianBlur(img, (self.ksize, self.ksize), self.sigma)

class ColorJitter:
    def __init__(self, brightness=0.0, contrast=0.0, saturation=0.0, hue=0.0, p: float = 0.5):
        self.brightness = brightness
        self.contrast = contrast
        self.saturation = saturation
        self.hue = hue
        self.p = p
    def __call__(self, img):
        if np.random.rand() >= self.p:
            return img
        out = img.astype(np.float32)
        if self.brightness > 1e-6:
            b = 1.0 + np.random.uniform(-self.brightness, self.brightness)
            out *= b
        if self.contrast > 1e-6:
            c = 1.0 + np.random.uniform(-self.contrast, self.contrast)
            mean = out.mean(axis=(0,1), keepdims=True)
            out = (out - mean) * c + mean
        out = np.clip(out, 0, 255)
        if self.saturation > 1e-6 or self.hue > 1e-6:
            hsv = cv2.cvtColor(out.astype(np.uint8), cv2.COLOR_RGB2HSV).astype(np.float32)
            if self.saturation > 1e-6:
                s_scale = 1.0 + np.random.uniform(-self.saturation, self.saturation)
                hsv[...,1] = np.clip(hsv[...,1] * s_scale, 0, 255)
            if self.hue > 1e-6:
                dh = np.random.uniform(-self.hue*180, self.hue*180)
                hsv[...,0] = (hsv[...,0] + dh) % 180
            out = cv2.cvtColor(hsv.astype(np.uint8), cv2.COLOR_HSV2RGB).astype(np.float32)
        return np.clip(out, 0, 255).astype(np.uint8)

class Normalize:
    def __init__(self, mean: List[float], std: List[float], max_pixel_value: float = 255.0):
        self.mean = np.array(mean, dtype=np.float32).reshape(1,1,3)
        self.std = np.array(std, dtype=np.float32).reshape(1,1,3)
        self.maxv = float(max_pixel_value)
    def __call__(self, img):
        x = img.astype(np.float32) / self.maxv
        x = (x - self.mean) / self.std
        return x.astype(np.float32)

def get_train_transforms():
    return Compose([
        RandomCrop(TARGET_SIZE, TARGET_SIZE),
        HorizontalFlip(p=0.5),
        VerticalFlip(p=0.5),
        Rotate(limit=25, p=0.5, border_mode=cv2.BORDER_CONSTANT, value=0),
        GaussianBlurTfm(ksize=3, sigma=0.0, p=0.25),
        ColorJitter(brightness=0.3, contrast=0.3, saturation=0.1, hue=0.05, p=0.6),
        Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD, max_pixel_value=255.0),
    ])

def get_valid_transforms():
    return Compose([
        CenterCrop(TARGET_SIZE, TARGET_SIZE),
        Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD, max_pixel_value=255.0),
    ])

# ---------- Dataset with Lazy Cache ----------
class RetinaDataset(Dataset):
    def __init__(self, ids: List[str], img_dir: Path, cache_dir: Path, labels: Optional[np.ndarray] = None, transform: Optional[Callable]=None):
        self.ids = ids
        self.img_dir = Path(img_dir)
        self.cache_dir = Path(cache_dir)
        self.labels = labels
        self.transform = transform

    def __len__(self):
        return len(self.ids)

    def _ensure_cached(self, img_id: str) -> Path:
        cached_path = self.cache_dir / f"{img_id}.png"
        if not cached_path.exists():
            src_path = self.img_dir / f"{img_id}.png"
            preprocess_and_cache_one(src_path, cached_path, CACHE_SIZE)
        return cached_path

    def __getitem__(self, idx: int):
        img_id = self.ids[idx]
        cpath = self._ensure_cached(img_id)
        img = cv2.imread(str(cpath), cv2.IMREAD_COLOR)
        img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        if self.transform is not None:
            img = self.transform(img)  # returns float32 HWC normalized
        if img.dtype != np.float32:
            img = img.astype(np.float32) / 255.0
        img = torch.from_numpy(img.transpose(2, 0, 1)).float()
        if self.labels is None:
            return img, img_id
        y = self.labels[idx]
        return img, y, img_id

# ---------- Backbones ----------
class ResNet18Regressor(nn.Module):
    def __init__(self, dropout: float = 0.2):
        super().__init__()
        import torchvision.models as tvm
        try:
            weights = tvm.ResNet18_Weights.IMAGENET1K_V1
        except AttributeError:
            weights = 'IMAGENET1K_V1'
        try:
            m = tvm.resnet18(weights=weights)
        except (urllib.error.URLError, urllib.error.HTTPError, OSError, ConnectionError, TimeoutError) as e:
            print(f'Warning: pretrained weights unavailable ({e}). Falling back to weights=None.')
            m = tvm.resnet18(weights=None)
        in_ch = m.fc.in_features
        m.fc = nn.Identity()
        self.backbone = m
        self.head = nn.Sequential(nn.Dropout(dropout), nn.Linear(in_ch, 1))
    def forward(self, x):
        x = self.backbone(x)
        return self.head(x).squeeze(1)

class ResNet34Regressor(nn.Module):
    def __init__(self, dropout: float = 0.2):
        super().__init__()
        import torchvision.models as tvm
        try:
            weights = tvm.ResNet34_Weights.IMAGENET1K_V1
        except AttributeError:
            weights = 'IMAGENET1K_V1'
        try:
            m = tvm.resnet34(weights=weights)
        except Exception as e:
            print(f'Warning: pretrained weights unavailable ({e}). Falling back to weights=None.')
            m = tvm.resnet34(weights=None)
        in_ch = m.fc.in_features
        m.fc = nn.Identity()
        self.backbone = m
        self.head = nn.Sequential(nn.Dropout(dropout), nn.Linear(in_ch, 1))
    def forward(self, x):
        x = self.backbone(x)
        return self.head(x).squeeze(1)

# ---------- Sampler ----------
def make_weighted_sampler(labels: np.ndarray) -> WeightedRandomSampler:
    classes, counts = np.unique(labels, return_counts=True)
    freq = {int(c): float(cnt) for c, cnt in zip(classes, counts)}
    weights_np = np.array([1.0 / freq[int(y)] for y in labels], dtype=np.float64)
    weights = torch.tensor(weights_np, dtype=torch.double)
    return WeightedRandomSampler(weights, num_samples=len(weights_np), replacement=True)

# ---------- Worker seeding ----------
def _seed_worker(worker_id: int):
    worker_seed = (SEED + worker_id) % 2**32
    np.random.seed(worker_seed)
    torch.manual_seed(worker_seed)

# ---------- Dataloader Factory ----------
def make_dataloaders(fold: int, batch_size: int = 16, num_workers: int = 4):
    df = pd.read_csv(FOLDS_CSV)
    trn = df[df['fold'] != fold].reset_index(drop=True)
    val = df[df['fold'] == fold].reset_index(drop=True)
    train_ids = trn['id_code'].tolist()
    val_ids = val['id_code'].tolist()
    y_tr = trn['diagnosis'].values.astype(int)
    y_va = val['diagnosis'].values.astype(int)

    train_tfms = get_train_transforms()
    valid_tfms = get_valid_transforms()
    train_ds = RetinaDataset(train_ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, y_tr, transform=train_tfms)
    valid_ds = RetinaDataset(val_ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, y_va, transform=valid_tfms)

    sampler = make_weighted_sampler(y_tr)
    pw = True if num_workers > 0 else False
    train_loader = DataLoader(
        train_ds, batch_size=batch_size, sampler=sampler, num_workers=num_workers, pin_memory=False,
        drop_last=True, persistent_workers=pw, worker_init_fn=_seed_worker if num_workers > 0 else None
    )
    valid_loader = DataLoader(
        valid_ds, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False,
        persistent_workers=pw, worker_init_fn=_seed_worker if num_workers > 0 else None
    )
    return train_loader, valid_loader, y_va, val_ids

print('Utilities ready: QWK, threshold optimizer, transforms, dataset (lazy cache), backbones (ResNet18/ResNet34), loaders (pin_memory=False).')

Utilities ready: QWK, threshold optimizer, transforms, dataset (lazy cache), backbones (ResNet18/ResNet34), loaders (pin_memory=False).


In [7]:
import time, json
from typing import Dict, Any, List, Tuple
import torch
import torch.nn as nn
from torch.optim import AdamW
from torch.optim.lr_scheduler import CosineAnnealingLR
from tqdm import tqdm
import numpy as np

try:
    torch.use_deterministic_algorithms(True, warn_only=True)
except Exception:
    pass

MODEL_NAME = 'res34_256px'  # artifact tag per audit
FORCE_CPU = False     # allow GPU to accelerate training if available

def _pick_device(min_free_bytes: int = 2*1024*1024*1024, wait_seconds: int = 1200, poll_seconds: int = 10) -> tuple[torch.device, bool]:
    if FORCE_CPU:
        return torch.device('cpu'), False
    if torch.cuda.is_available():
        deadline = time.time() + max(0, wait_seconds)
        while True:
            try:
                free, total = torch.cuda.mem_get_info()
                if free >= min_free_bytes:
                    return torch.device('cuda'), True
                if time.time() >= deadline:
                    print(f'GPU wait timeout. Free {free/1024**3:.2f}GB < required {(min_free_bytes/1024**3):.2f}GB. Falling back to CPU.')
                    return torch.device('cpu'), False
                print(f'Waiting for GPU: free {free/1024**3:.2f}GB / {total/1024**3:.2f}GB; need {(min_free_bytes/1024**3):.2f}GB. Retrying in {poll_seconds}s...')
                time.sleep(poll_seconds)
            except Exception:
                return torch.device('cuda'), True
    return torch.device('cpu'), False

def _set_lr(optimizer, lr):
    for pg in optimizer.param_groups:
        pg['lr'] = lr

def train_one_fold(fold: int, epochs: int = 20, batch_size: int = 4, lr: float = 3e-4, wd: float = 1e-4, grad_clip: float = 1.0, num_workers: int = 0, patience: int = 5, init_th: List[float] | None = None, model_name: str = MODEL_NAME, force_amp: bool | None = None) -> Dict[str, Any]:
    set_seed(SEED + fold)
    device, can_amp = _pick_device()
    train_loader, valid_loader, y_va, val_ids = make_dataloaders(fold, batch_size=batch_size, num_workers=num_workers)

    # Mandated backbone: ResNet34 (pretrained if available)
    model = ResNet34Regressor(dropout=0.2)
    # Try enabling grad checkpointing if available (torchvision may ignore)
    if hasattr(model, 'backbone') and hasattr(model.backbone, 'gradient_checkpointing_enable'):
        try:
            model.backbone.gradient_checkpointing_enable()
            print('[Fold', str(fold)+'] Enabled gradient checkpointing on backbone')
        except Exception:
            pass
    model = model.to(device)

    opt = AdamW(model.parameters(), lr=lr, weight_decay=wd)
    use_amp = (can_amp if force_amp is None else (force_amp and can_amp))
    print(f'[Fold {fold}] device={device.type} AMP={use_amp} BS={batch_size} epochs={epochs}')
    scaler = torch.amp.GradScaler('cuda', enabled=use_amp)
    cos_epochs = max(1, epochs - 1)  # cosine after 1-epoch warmup
    scheduler = CosineAnnealingLR(opt, T_max=cos_epochs)
    crit = nn.SmoothL1Loss(reduction='mean')

    best_qwk = -1.0
    best_state = None
    best_th = init_th if init_th is not None else [0.2, 0.4, 0.6, 0.8]
    bad = 0

    base_lr = lr
    for ep in range(1, epochs + 1):
        model.train()
        # Warmup epoch at 0.1x LR
        if ep == 1:
            _set_lr(opt, base_lr * 0.1)
        tr_loss_sum = 0.0
        seen = 0
        pbar = tqdm(train_loader, desc=f'Fold{fold} Ep{ep}/{epochs} train', leave=False)
        for batch in pbar:
            imgs, ys, _ids = batch
            imgs = imgs.to(device, non_blocking=True)
            ys = ys.float().to(device, non_blocking=True)
            opt.zero_grad(set_to_none=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    preds = model(imgs)
                    loss = crit(preds, ys)
                scaler.scale(loss).backward()
                if grad_clip is not None:
                    scaler.unscale_(opt)
                    nn.utils.clip_grad_norm_(model.parameters(), grad_clip)
                scaler.step(opt)
                scaler.update()
            else:
                preds = model(imgs)
                loss = crit(preds, ys)
                loss.backward()
                if grad_clip is not None:
                    nn.utils.clip_grad_norm_(model.parameters(), grad_clip)
                opt.step()
            bs = imgs.size(0)
            tr_loss_sum += loss.item() * bs
            seen += bs
        tr_loss = tr_loss_sum / max(1, seen)

        # Step scheduler after warmup
        if ep == 1:
            _set_lr(opt, base_lr)
        else:
            scheduler.step()

        model.eval()
        all_preds = []
        with torch.inference_mode():
            for batch in tqdm(valid_loader, desc=f'Fold{fold} Ep{ep}/{epochs} valid', leave=False):
                imgs, ys, _ids = batch
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p = model(imgs)
                else:
                    p = model(imgs)
                all_preds.append(p.detach().float().cpu())
        all_preds = torch.cat(all_preds).numpy().reshape(-1)
        th = optimize_thresholds(all_preds, y_va, init=best_th, n_iter=8)
        preds_lbl = preds_to_labels_reg(all_preds, th)
        qwk = qwk_score(y_va, preds_lbl)

        print(f'Epoch {ep}: train_loss={tr_loss:.4f} val_qwk={qwk:.4f} th={[round(float(x),4) for x in th]}')

        if qwk > best_qwk + 1e-5:
            best_qwk = qwk
            best_state = {k: v.cpu() for k, v in model.state_dict().items()}
            best_th = th
            bad = 0
            # Standardized artifact name
            torch.save(best_state, f'model_{model_name}_fold{fold}.pth')
            try:
                import numpy as _np
                _np.save(f"thresholds_{model_name}_fold{fold}.npy", _np.array(best_th, dtype=_np.float32))
            except Exception:
                pass
        else:
            bad += 1
            if bad >= patience:
                print('Early stopping.')
                break

    if best_state is not None:
        model.load_state_dict(best_state)

    model.eval()
    val_preds = []
    pw = True if num_workers > 0 else False
    with torch.inference_mode():
        for batch in DataLoader(valid_loader.dataset, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False, persistent_workers=pw, worker_init_fn=_seed_worker if num_workers>0 else None):
            imgs, ys, _ids = batch
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    p = model(imgs)
            else:
                p = model(imgs)
            val_preds.append(p.detach().float().cpu())
    val_preds = torch.cat(val_preds).numpy().reshape(-1)

    # Cleanup loaders to free memory
    del train_loader, valid_loader
    if torch.cuda.is_available():
        torch.cuda.empty_cache()

    return {
        'model': model,
        'optimizer': opt,
        'scheduler': scheduler,
        'best_qwk': best_qwk,
        'best_th': best_th,
        'y_va': y_va,
        'val_ids': val_ids,
        'val_preds': val_preds
    }

def infer_test_preds(model: nn.Module, test_ids: List[str], batch_size: int = 8, num_workers: int = 0, tta: int = 4) -> np.ndarray:
    device, can_amp = _pick_device(min_free_bytes=2*1024*1024*1024)
    ds = RetinaDataset(test_ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    pw = True if num_workers > 0 else False
    dl = DataLoader(ds, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False,
                    persistent_workers=pw, worker_init_fn=_seed_worker if num_workers>0 else None)
    model = model.to(device).eval()
    preds = []
    use_amp = can_amp
    # If CPU device, disable TTA to avoid timeouts
    if device.type == 'cpu':
        tta = 0
    with torch.inference_mode():
        for batch in tqdm(dl, desc='Test infer', leave=False):
            imgs, id_batch = batch
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    p0 = model(imgs)
            else:
                p0 = model(imgs)
            if tta and tta >= 4:
                imgs_h = torch.flip(imgs, dims=[3])
                imgs_v = torch.flip(imgs, dims=[2])
                imgs_hv = torch.flip(imgs, dims=[2, 3])
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p_h = model(imgs_h)
                        p_v = model(imgs_v)
                        p_hv = model(imgs_hv)
                else:
                    p_h = model(imgs_h)
                    p_v = model(imgs_v)
                    p_hv = model(imgs_hv)
                p = (p0 + p_h + p_v + p_hv) / 4.0
            elif tta and tta == 3:
                imgs_h = torch.flip(imgs, dims=[3])
                imgs_v = torch.flip(imgs, dims=[2])
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p_h = model(imgs_h)
                        p_v = model(imgs_v)
                else:
                    p_h = model(imgs_h)
                    p_v = model(imgs_v)
                p = (p0 + p_h + p_v) / 3.0
            elif tta and tta == 2:
                imgs_h = torch.flip(imgs, dims=[3])
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p_h = model(imgs_h)
                else:
                    p_h = model(imgs_h)
                p = (p0 + p_h) / 2.0
            else:
                p = p0
            preds.append(p.detach().float().cpu())
    preds = torch.cat(preds).numpy().reshape(-1)
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    return preds

# Final run config
NUM_FOLDS = 5
EPOCHS = 20
BATCH_SIZE = 4
NUM_WORKERS = 0
LR = 3e-4
WD = 1e-4
PATIENCE = 5

# Verify folds file
assert FOLDS_CSV.exists(), 'folds_seed42_k5.csv missing.'
df_f = pd.read_csv(FOLDS_CSV)
assert 'fold' in df_f.columns and 'diagnosis' in df_f.columns and 'id_code' in df_f.columns, 'Folds file missing required columns.'
u_folds = sorted(df_f['fold'].unique().tolist())
assert u_folds == [0,1,2,3,4], f'Unexpected folds present: {u_folds}'
print('Fold label distribution check:')
print(df_f.groupby('fold')['diagnosis'].value_counts().unstack(fill_value=0))

# Ensure cache exists (no-op if already cached)
build_cache('train')
build_cache('test')

df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()

oof_preds_all = []
oof_y_all = []
oof_ids_all = []
test_preds_accum = None
prev_best_th = None
best_ths_all: List[List[float]] = []

for fold in range(NUM_FOLDS):
    try:
        res = train_one_fold(fold, epochs=EPOCHS, batch_size=BATCH_SIZE, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=None)
    except RuntimeError as e:
        msg = str(e)
        if ('CUDA out of memory' in msg) or ('CUBLAS_STATUS_ALLOC_FAILED' in msg) or ('CUDA error' in msg):
            print(f'Fold {fold}: CUDA error encountered. Retrying with AMP disabled...')
            if torch.cuda.is_available():
                torch.cuda.empty_cache()
            try:
                res = train_one_fold(fold, epochs=EPOCHS, batch_size=BATCH_SIZE, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=False)
            except RuntimeError as e2:
                print(f'Fold {fold}: Still failing. Retrying on GPU with batch_size=2...')
                if torch.cuda.is_available():
                    torch.cuda.empty_cache()
                try:
                    res = train_one_fold(fold, epochs=EPOCHS, batch_size=2, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=False)
                except RuntimeError as e3:
                    print(f'Fold {fold}: Still failing. Retrying on GPU with batch_size=1...')
                    if torch.cuda.is_available():
                        torch.cuda.empty_cache()
                    try:
                        res = train_one_fold(fold, epochs=EPOCHS, batch_size=1, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=False)
                    except RuntimeError as e4:
                        print(f'Fold {fold}: GPU retries exhausted. Falling back to CPU (batch_size=2)...')
                        if torch.cuda.is_available():
                            torch.cuda.empty_cache()
                        FORCE_CPU = True
                        try:
                            res = train_one_fold(fold, epochs=EPOCHS, batch_size=2, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=False)
                        finally:
                            FORCE_CPU = False
        else:
            raise
    except RuntimeError as e:
        msg = str(e)
        print(f'Fold {fold}: RuntimeError: {msg}. Retrying with batch_size=2 and AMP disabled...')
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
        res = train_one_fold(fold, epochs=EPOCHS, batch_size=2, lr=LR, wd=WD, grad_clip=1.0, num_workers=NUM_WORKERS, patience=PATIENCE, init_th=prev_best_th, model_name=MODEL_NAME, force_amp=False)

    print(f'Fold {fold} best QWK: {res["best_qwk"]:.4f} with th={[round(float(x),4) for x in res["best_th"]]}')
    oof_preds_all.append(res['val_preds'])
    oof_y_all.append(res['y_va'])
    oof_ids_all.extend(res['val_ids'])
    prev_best_th = res['best_th']
    best_ths_all.append(res['best_th'])
    fold_test_preds = infer_test_preds(res['model'], test_ids, batch_size=8, num_workers=0, tta=4)
    if test_preds_accum is None:
        test_preds_accum = fold_test_preds
    else:
        test_preds_accum += fold_test_preds
    model = res['model']
    optimizer = res['optimizer']
    scheduler = res['scheduler']
    del model, optimizer, scheduler
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    import gc; gc.collect()

oof_preds_all = np.concatenate(oof_preds_all)
oof_y_all = np.concatenate(oof_y_all).astype(int)
test_preds_mean = test_preds_accum / float(NUM_FOLDS)

# Optimize global thresholds on concatenated OOF using median of per-fold best thresholds as init
if len(best_ths_all) > 0:
    init_global = np.median(np.array(best_ths_all, dtype=np.float32), axis=0).tolist()
else:
    init_global = None
global_th = optimize_thresholds(oof_preds_all, oof_y_all, init=init_global, n_iter=50)
oof_labels = preds_to_labels_reg(oof_preds_all, global_th)
oof_qwk = qwk_score(oof_y_all, oof_labels)
print('Global OOF QWK:', round(float(oof_qwk), 5), ' Global thresholds:', [round(float(x),4) for x in global_th])

# Save artifacts for audit and analysis
np.save('oof_preds.npy', oof_preds_all)
np.save('oof_y.npy', oof_y_all)
pd.DataFrame({'id_code': oof_ids_all, 'oof_pred': oof_preds_all, 'oof_label': oof_labels}).to_csv('oof_predictions.csv', index=False)
with open('global_thresholds.json', 'w') as f:
    json.dump({'thresholds': [float(x) for x in global_th], 'oof_qwk': float(oof_qwk), 'model': MODEL_NAME}, f, indent=2)

# Build submission from averaged test predictions with global thresholds
test_labels = preds_to_labels_reg(test_preds_mean, global_th).astype(int)
sub = pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels})
sub.to_csv('submission.csv', index=False)
print('Saved submission.csv with', len(sub), 'rows')

Fold label distribution check:
diagnosis    0   1    2   3   4
fold                           
0          326  68  180  36  51
1          326  68  179  35  51
2          326  68  179  35  51
3          325  68  179  35  51
4          325  68  179  35  51


Caching train images:   0%|          | 0/3295 [00:00<?, ?it/s]

Caching train images: 100%|██████████| 3295/3295 [00:00<00:00, 93115.70it/s]

Caching test images:   0%|          | 0/367 [00:00<?, ?it/s]

Caching test images: 100%|██████████| 367/367 [00:00<00:00, 84824.47it/s]

...

Test infer:  87%|████████▋ | 40/46 [00:02<00:00, 18.28it/s]

Test infer:  91%|█████████▏| 42/46 [00:02<00:00, 17.15it/s]

Test infer:  96%|█████████▌| 44/46 [00:02<00:00, 16.12it/s]

Test infer: 100%|██████████| 46/46 [00:02<00:00, 16.19it/s]

Global OOF QWK: 0.86381  Global thresholds: [0.6012, 0.9178, 2.5811, 3.915]
Saved submission.csv with 367 rows


In [2]:
# Lightweight init: re-define globals without pip installs
import os, random
from pathlib import Path
import numpy as np
import pandas as pd
import torch

def set_seed(seed: int = 42):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    os.environ['PYTHONHASHSEED'] = str(seed)

SEED = 42
set_seed(SEED)

CWD = Path.cwd()
DATA_DIR = CWD
TRAIN_IMG_DIR = DATA_DIR / 'train_images'
TEST_IMG_DIR = DATA_DIR / 'test_images'
TRAIN_CSV = DATA_DIR / 'train.csv'
TEST_CSV = DATA_DIR / 'test.csv'
SAMPLE_SUB = DATA_DIR / 'sample_submission.csv'
FOLDS_CSV = DATA_DIR / 'folds_seed42_k5.csv'

# Contingency: reduce resolution to 256 (cache 288) to avoid GPU OOM
CACHE_DIR = DATA_DIR / 'cache_256_retina_v1'
IMG_SIZE = 256
TARGET_SIZE = IMG_SIZE
IMAGENET_MEAN = [0.485, 0.456, 0.406]
IMAGENET_STD  = [0.229, 0.224, 0.225]

# Cache subdirs for 288 cache size and 256 crop
CACHE_TRAIN_DIR = CACHE_DIR / 'train_288'
CACHE_TEST_DIR  = CACHE_DIR / 'test_288'

print('Globals set (256px). TEST_CSV exists:', TEST_CSV.exists(), 'FOLDS exists:', FOLDS_CSV.exists(), 'TARGET_SIZE:', TARGET_SIZE, 'CACHE_DIR:', str(CACHE_DIR))

Globals set (256px). TEST_CSV exists: True FOLDS exists: True TARGET_SIZE: 256 CACHE_DIR: /app/agent_run_states/aptos2019-blindness-detection/cache_256_retina_v1


In [5]:
# GPU check before training per audit
import torch
print('CUDA available:', torch.cuda.is_available())
if torch.cuda.is_available():
    print('GPU count:', torch.cuda.device_count())
    print('GPU name:', torch.cuda.get_device_name(0))
    props = torch.cuda.get_device_properties(0)
    print('Total GPU Memory (GB):', round(props.total_memory/1024**3, 2))
    try:
        torch.cuda.empty_cache()
        print('\nMemory summary before training:')
        print(torch.cuda.memory_summary(device=None, abbreviated=True))
    except Exception as e:
        print('memory_summary unavailable:', repr(e))
else:
    print('Running on CPU.')

CUDA available: True
GPU count: 1
GPU name: Tesla V100-SXM2-16GB
Total GPU Memory (GB): 15.77

Memory summary before training:
|===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 0            |        cudaMalloc retries: 0         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |      0 B   |      0 B   |      0 B   |      0 B   |
|---------------------------------------------------------------------------|
| Active memory         |      0 B   |      0 B   |      0 B   |      0 B   |
|---------------------------------------------------------------------------|
| Requested mem

In [8]:
# Re-optimize global thresholds with scipy and rebuild submission using saved fold models
import json, math, sys, subprocess, time
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from pathlib import Path

# Ensure scipy is available
try:
    import scipy.optimize as sopt
except Exception:
    subprocess.run([sys.executable, '-m', 'pip', 'install', '-q', 'scipy>=1.10.0'])
    import scipy.optimize as sopt

# Utilities from notebook context: qwk_score, preds_to_labels_reg, RetinaDataset, get_valid_transforms, ResNet34Regressor, _seed_worker

def _enforce_monotonic(th):
    th = list(th)
    th[1] = max(th[1], th[0] + 1e-4)
    th[2] = max(th[2], th[1] + 1e-4)
    th[3] = max(th[3], th[2] + 1e-4)
    return th

def qwk_objective(th, preds, y_true):
    th = _enforce_monotonic(th)
    labels = preds_to_labels_reg(preds, th)
    # Negative for maximization
    return -qwk_score(y_true, labels)

def optimize_thresholds_scipy(preds: np.ndarray, y_true: np.ndarray, inits: list[list[float]], method: str = 'Nelder-Mead', maxiter: int = 1000) -> tuple[list[float], float]:
    best_th, best_q = None, -1e9
    bounds = None  # unconstrained with monotonic enforcement inside objective
    for init in inits:
        init = _enforce_monotonic(init)
        res = sopt.minimize(qwk_objective, x0=np.array(init, dtype=np.float64), args=(preds, y_true), method=method, options={'maxiter': maxiter, 'xatol': 1e-6, 'fatol': 1e-6})
        th = _enforce_monotonic(res.x.tolist())
        q = -res.fun
        if q > best_q:
            best_q, best_th = q, th
    return best_th, float(best_q)

# Load OOF predictions and labels
oof_preds = np.load('oof_preds.npy') if Path('oof_preds.npy').exists() else None
oof_y = np.load('oof_y.npy') if Path('oof_y.npy').exists() else None
assert oof_preds is not None and oof_y is not None, 'Missing OOF artifacts.'

# Build multiple initializations
inits = []
try:
    with open('global_thresholds.json', 'r') as f:
        j = json.load(f)
        inits.append(j.get('thresholds', []))
except Exception:
    pass
q_inits = np.quantile(oof_preds, [0.2, 0.4, 0.6, 0.8]).tolist()
inits.append(q_inits)
try:
    th_files = sorted(list(Path('.').glob('thresholds_*fold*.npy')))
    if th_files:
        ths = [np.load(p) for p in th_files]
        if len(ths) > 0:
            med = np.median(np.vstack(ths), axis=0).tolist()
            mean = np.mean(np.vstack(ths), axis=0).tolist()
            inits.extend([med, mean])
except Exception:
    pass
# Add a few jittered variants
for scale in [0.1, 0.2, 0.3]:
    noise = (np.random.randn(4) * (oof_preds.std() + 1e-6) * scale).tolist()
    inits.append([q_inits[i] + noise[i] for i in range(4)])

# Deduplicate inits
uniq = []
seen = set()
for th in inits:
    if not th or len(th) != 4:
        continue
    key = tuple(np.round(th, 4))
    if key not in seen:
        seen.add(key)
        uniq.append(list(th))
inits = uniq[:10] if len(uniq) > 10 else uniq

best_th, best_q = optimize_thresholds_scipy(oof_preds, oof_y, inits=inits, method='Nelder-Mead', maxiter=2000)
print('SciPy-optimized OOF QWK:', round(best_q, 6), ' thresholds:', [round(float(x), 6) for x in best_th])

# Save improved thresholds
with open('global_thresholds_scipy.json', 'w') as f:
    json.dump({'thresholds': [float(x) for x in best_th], 'oof_qwk': float(best_q), 'model': 'res34_256px'}, f, indent=2)

# Rebuild test predictions by loading saved fold models and averaging
df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()
from math import ceil

def _infer_model_on_test(model: nn.Module, ids: list[str], bs: int = 16) -> np.ndarray:
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    model = model.to(device).eval()
    preds = []
    use_amp = torch.cuda.is_available()
    with torch.inference_mode():
        for batch in dl:
            imgs, id_batch = batch
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    p = model(imgs)
            else:
                p = model(imgs)
            preds.append(p.detach().float().cpu())
    return torch.cat(preds).numpy().reshape(-1)

fold_preds = []
for fold in range(5):
    ckpt = Path(f'model_res34_256px_fold{fold}.pth')
    if not ckpt.exists():
        print(f'Warning: missing {ckpt}, skipping this fold in inference.')
        continue
    m = ResNet34Regressor(dropout=0.2)
    sd = torch.load(ckpt, map_location='cpu')
    m.load_state_dict(sd, strict=True)
    p = _infer_model_on_test(m, test_ids, bs=32)
    fold_preds.append(p)
    del m, sd
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
import gc; gc.collect()

assert len(fold_preds) > 0, 'No fold predictions computed.'
test_preds_mean = np.mean(np.vstack(fold_preds), axis=0)

# Apply improved thresholds to build submission
test_labels = preds_to_labels_reg(test_preds_mean, best_th).astype(int)
sub = pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels})
sub.to_csv('submission.csv', index=False)
print('submission.csv saved with', len(sub), 'rows; OOF QWK (scipy):', round(best_q, 6))

SciPy-optimized OOF QWK: 0.86381  thresholds: [0.601158, 0.91779, 2.581106, 3.915026]


/tmp/ipykernel_2492/298120887.py:124: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


submission.csv saved with 367 rows; OOF QWK (scipy): 0.86381


In [9]:
# 384px dry-run with gradient accumulation to validate GPU memory before fine-tune
import os, time
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch.optim import AdamW
from torch.utils.data import DataLoader

# Switch globals to 384px and new cache
IMG_SIZE = 384
TARGET_SIZE = IMG_SIZE
CACHE_DIR = DATA_DIR / 'cache_384_retina_v1'
CACHE_TRAIN_DIR = CACHE_DIR / 'train_416'
CACHE_TEST_DIR  = CACHE_DIR / 'test_416'
CACHE_SIZE = 416  # TARGET_SIZE + 32
os.makedirs(CACHE_TRAIN_DIR, exist_ok=True)
os.makedirs(CACHE_TEST_DIR, exist_ok=True)
print('384px config set. TARGET_SIZE=', TARGET_SIZE, ' CACHE_SIZE=', CACHE_SIZE, ' CACHE_DIR=', str(CACHE_DIR))

# Build a tiny cache subset for dry-run
build_cache('train', limit=32)
build_cache('test', limit=16)

# Make loaders for a single fold with small batch
fold = 0
bs_phys = 2  # physical batch size
accum_steps = 4  # effective batch = bs_phys * accum_steps
train_loader, valid_loader, y_va, val_ids = make_dataloaders(fold, batch_size=bs_phys, num_workers=0)

# Pick device with higher free VRAM requirement for 384px
device, can_amp = (torch.device('cuda'), True) if torch.cuda.is_available() else (torch.device('cpu'), False)
if device.type == 'cuda':
    deadline = time.time() + 600
    while True:
        free, total = torch.cuda.mem_get_info()
        if free >= 4*1024*1024*1024:
            break
        if time.time() > deadline:
            print(f'GPU wait timeout at 384px. Free {free/1024**3:.2f}GB < 4.00GB. Aborting dry-run.')
            raise SystemExit(0)
        print(f'Waiting GPU for dry-run: free {free/1024**3:.2f}GB / {total/1024**3:.2f}GB; need 4.00GB...')
        time.sleep(10)

# Model + optimizer
model = ResNet34Regressor(dropout=0.2).to(device)
opt = AdamW(model.parameters(), lr=1e-4, weight_decay=1e-4)
crit = nn.SmoothL1Loss()
scaler = torch.amp.GradScaler('cuda', enabled=can_amp)
model.train()

# One accumulated step over a few mini-batches
total_loss = 0.0
steps = 0
for i, (imgs, ys, _ids) in enumerate(train_loader):
    imgs = imgs.to(device, non_blocking=True)
    ys = ys.float().to(device, non_blocking=True)
    with torch.amp.autocast('cuda', enabled=can_amp):
        preds = model(imgs)
        loss = crit(preds, ys) / accum_steps
    scaler.scale(loss).backward()
    total_loss += loss.item()
    if (i + 1) % accum_steps == 0:
        scaler.unscale_(opt)
        nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        scaler.step(opt)
        scaler.update()
        opt.zero_grad(set_to_none=True)
        steps += 1
    if steps >= 1:
        break

print('384px dry-run OK. AMP=', can_amp, ' phys_BS=', bs_phys, ' accum_steps=', accum_steps, ' device=', device.type)
del model, opt, scaler, train_loader, valid_loader
if torch.cuda.is_available():
    torch.cuda.empty_cache()

384px config set. TARGET_SIZE= 384  CACHE_SIZE= 416  CACHE_DIR= /app/agent_run_states/aptos2019-blindness-detection/cache_384_retina_v1


Caching train images:   0%|          | 0/32 [00:00<?, ?it/s]

Caching train images: 100%|██████████| 32/32 [00:00<00:00, 53430.62it/s]

Caching test images:   0%|          | 0/16 [00:00<?, ?it/s]

Caching test images: 100%|██████████| 16/16 [00:00<00:00, 48806.45it/s]

...

Waiting GPU for dry-run: free 0.56GB / 15.77GB; need 4.00GB...


Waiting GPU for dry-run: free 0.52GB / 15.77GB; need 4.00GB...


GPU wait timeout at 384px. Free 0.52GB < 4.00GB. Aborting dry-run.


SystemExit: 0

/usr/local/lib/python3.11/dist-packages/IPython/core/interactiveshell.py:3707: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [14]:
# Joint calibration (scale/shift) + threshold optimization with SciPy; rebuild submission
import json, sys, subprocess
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from pathlib import Path
from torch.utils.data import DataLoader

# Ensure scipy
try:
    import scipy.optimize as sopt
except Exception:
    subprocess.run([sys.executable, '-m', 'pip', 'install', '-q', 'scipy>=1.10.0'])
    import scipy.optimize as sopt

# Load OOF
oof_preds = np.load('oof_preds.npy')
oof_y = np.load('oof_y.npy').astype(int)

def _enforce_mono(th):
    th = list(th)
    th[1] = max(th[1], th[0] + 1e-4)
    th[2] = max(th[2], th[1] + 1e-4)
    th[3] = max(th[3], th[2] + 1e-4)
    return th

def apply_affine(x, a, b):
    return a * x + b

def qwk_score_np(y_true: np.ndarray, y_pred: np.ndarray, n_classes: int = 5) -> float:
    y_true = y_true.astype(int).ravel()
    y_pred = y_pred.astype(int).ravel()
    O = np.zeros((n_classes, n_classes), dtype=np.float64)
    for t, p in zip(y_true, y_pred):
        if 0 <= t < n_classes and 0 <= p < n_classes:
            O[t, p] += 1
    N = O.sum()
    if N == 0:
        return 0.0
    hist_true = O.sum(axis=1)
    hist_pred = O.sum(axis=0)
    E = np.outer(hist_true, hist_pred) / (N + 1e-12)
    W = np.zeros((n_classes, n_classes), dtype=np.float64)
    for i in range(n_classes):
        for j in range(n_classes):
            W[i, j] = ((i - j) ** 2) / ((n_classes - 1) ** 2)
    num = (W * O).sum()
    den = (W * E).sum() + 1e-12
    return 1.0 - num / den

def preds_to_labels_reg_np(preds: np.ndarray, th):
    t0, t1, t2, t3 = th
    return np.digitize(preds, bins=[t0, t1, t2, t3]).astype(int)

def objective(params, preds, y_true):
    a, b = params[0], params[1]
    th = _enforce_mono(params[2:6])
    x = apply_affine(preds, a, b)
    labels = preds_to_labels_reg_np(x, th)
    return -qwk_score_np(y_true, labels)

# Initializations
inits = []
try:
    with open('global_thresholds.json', 'r') as f:
        base_th = json.load(f).get('thresholds', None)
except Exception:
    base_th = None
if base_th is None or len(base_th) != 4:
    base_th = np.quantile(oof_preds, [0.2, 0.4, 0.6, 0.8]).tolist()
for a0 in [0.8, 1.0, 1.2]:
    for b0 in [-0.2, 0.0, 0.2]:
        inits.append([a0, b0] + list(base_th))

best_val = 1e9
best_params = None
for init in inits:
    res = sopt.minimize(objective, x0=np.array(init, dtype=np.float64), args=(oof_preds, oof_y), method='Nelder-Mead', options={'maxiter': 3000, 'xatol': 1e-6, 'fatol': 1e-6})
    if res.fun < best_val:
        best_val = float(res.fun)
        best_params = res.x.copy()

a_opt, b_opt = best_params[0], best_params[1]
th_opt = _enforce_mono(best_params[2:6].tolist())
oof_cal = apply_affine(oof_preds, a_opt, b_opt)
oof_labels = preds_to_labels_reg_np(oof_cal, th_opt)
oof_qwk_cal = qwk_score_np(oof_y, oof_labels)
print('Calibrated OOF QWK:', round(float(oof_qwk_cal), 6), ' a=', round(float(a_opt),6), ' b=', round(float(b_opt),6), ' th=', [round(float(x),6) for x in th_opt])

# Recompute test predictions from saved fold models and apply calibration+thresholds
df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()

def infer_fold_preds(ids):
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=32, shuffle=False, num_workers=0, pin_memory=False)
    preds_all = []
    for fold in range(5):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        ps = []
        with torch.inference_mode():
            for batch in dl:
                imgs, idb = batch
                imgs = imgs.to(device, non_blocking=True)
                with torch.amp.autocast('cuda', enabled=torch.cuda.is_available()):
                    p = m(imgs)
                ps.append(p.detach().float().cpu())
        preds_all.append(torch.cat(ps).numpy().reshape(-1))
        del m, sd; 
        torch.cuda.empty_cache() if torch.cuda.is_available() else None
    assert len(preds_all) > 0, 'No fold checkpoints found.'
    return np.mean(np.vstack(preds_all), axis=0)

test_preds_mean = infer_fold_preds(test_ids)
test_preds_cal = apply_affine(test_preds_mean, a_opt, b_opt)
test_labels = preds_to_labels_reg_np(test_preds_cal, th_opt).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels}).to_csv('submission.csv', index=False)
with open('global_thresholds_scipy.json', 'w') as f:
    json.dump({'thresholds': [float(x) for x in th_opt], 'oof_qwk': float(oof_qwk_cal), 'a': float(a_opt), 'b': float(b_opt)}, f, indent=2)
print('submission.csv saved with', len(test_labels), 'rows; calibrated OOF QWK:', round(float(oof_qwk_cal), 6))

Calibrated OOF QWK: 0.86381  a= 1.0  b= 0.0  th= [0.601158, 0.91779, 2.581106, 3.915026]


/tmp/ipykernel_2492/1972561728.py:105: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


submission.csv saved with 367 rows; calibrated OOF QWK: 0.86381


In [11]:
# ResNet34 Ordinal (CORAL-style) 256px 5-fold training + blend with regression
import json, time
from typing import List, Dict, Any
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch.optim import AdamW
from torch.optim.lr_scheduler import CosineAnnealingLR
from torch.utils.data import DataLoader
from tqdm import tqdm
from pathlib import Path

# ----- Ordinal model (4 logits for P(y>k)) -----
class ResNet34Ordinal(nn.Module):
    def __init__(self, dropout: float = 0.2):
        super().__init__()
        import torchvision.models as tvm
        try:
            weights = tvm.ResNet34_Weights.IMAGENET1K_V1
        except AttributeError:
            weights = 'IMAGENET1K_V1'
        try:
            m = tvm.resnet34(weights=weights)
        except Exception as e:
            print(f'Warning: pretrained weights unavailable ({e}). Falling back to weights=None.')
            m = tvm.resnet34(weights=None)
        in_ch = m.fc.in_features
        m.fc = nn.Identity()
        self.backbone = m
        self.head = nn.Sequential(nn.Dropout(dropout), nn.Linear(in_ch, 4))
    def forward(self, x):
        x = self.backbone(x)
        logits = self.head(x)
        return logits  # shape [B,4]
    def predict_score(self, x):
        logits = self.forward(x)
        return torch.sigmoid(logits).sum(dim=1)  # continuous score in [0,4]

def make_pos_weights(y: np.ndarray) -> torch.Tensor:
    # y in {0..4}; create 4 binary tasks for y>k
    pos_w = []
    n = len(y)
    for k in range(4):
        pos = float((y > k).sum())
        neg = float(n - pos)
        if pos < 0.5:
            w = 1.0
        else:
            w = neg / max(pos, 1.0)
        pos_w.append(w)
    return torch.tensor(pos_w, dtype=torch.float32)

# ----- Local dataloader factory without WeightedRandomSampler (per audit fix) -----
def make_dataloaders_ordinal(fold: int, batch_size: int = 16, num_workers: int = 0):
    df = pd.read_csv(FOLDS_CSV)
    trn = df[df['fold'] != fold].reset_index(drop=True)
    val = df[df['fold'] == fold].reset_index(drop=True)
    train_ids = trn['id_code'].tolist()
    val_ids = val['id_code'].tolist()
    y_tr = trn['diagnosis'].values.astype(int)
    y_va = val['diagnosis'].values.astype(int)
    train_tfms = get_train_transforms()
    valid_tfms = get_valid_transforms()
    train_ds = RetinaDataset(train_ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, y_tr, transform=train_tfms)
    valid_ds = RetinaDataset(val_ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, y_va, transform=valid_tfms)
    pw = True if num_workers > 0 else False
    train_loader = DataLoader(
        train_ds, batch_size=batch_size, shuffle=True, num_workers=num_workers, pin_memory=False,
        drop_last=False, persistent_workers=pw, worker_init_fn=_seed_worker if num_workers > 0 else None
    )
    valid_loader = DataLoader(
        valid_ds, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False,
        persistent_workers=pw, worker_init_fn=_seed_worker if num_workers > 0 else None
    )
    return train_loader, valid_loader, y_va, val_ids

def train_one_fold_ordinal(fold: int, epochs: int = 20, batch_size: int = 4, lr: float = 1e-4, wd: float = 1e-4, grad_clip: float = 1.0, num_workers: int = 0, patience: int = 5, init_th: List[float] | None = None, model_name: str = 'res34_ordinal_256px', force_amp: bool | None = None) -> Dict[str, Any]:
    set_seed(SEED + 100 + fold)
    device, can_amp = _pick_device()
    # Use sampler-free loaders for ordinal
    train_loader, valid_loader, y_va, val_ids = make_dataloaders_ordinal(fold, batch_size=batch_size, num_workers=num_workers)

    model = ResNet34Ordinal(dropout=0.2)
    if hasattr(model, 'backbone') and hasattr(model.backbone, 'gradient_checkpointing_enable'):
        try:
            model.backbone.gradient_checkpointing_enable()
            print('[Fold', str(fold)+'] Enabled gradient checkpointing (ordinal)')
        except Exception:
            pass
    model = model.to(device)

    pos_w = make_pos_weights(np.array([train_loader.dataset.labels[i] for i in range(len(train_loader.dataset))]))
    pos_w = pos_w.to(device)
    criterion = nn.BCEWithLogitsLoss(pos_weight=pos_w)
    opt = AdamW(model.parameters(), lr=lr, weight_decay=wd)
    use_amp = (can_amp if force_amp is None else (force_amp and can_amp))
    scaler = torch.amp.GradScaler('cuda', enabled=use_amp)
    cos_epochs = max(1, epochs - 1)
    scheduler = CosineAnnealingLR(opt, T_max=cos_epochs)
    print(f'[Ordinal Fold {fold}] device={device.type} AMP={use_amp} BS={batch_size} epochs={epochs}')

    best_qwk = -1.0
    best_state = None
    best_th = init_th if init_th is not None else [0.5, 1.5, 2.5, 3.5]
    bad = 0
    base_lr = lr

    for ep in range(1, epochs + 1):
        model.train()
        # warmup at 0.1x for stability
        if ep == 1:
            _set_lr(opt, base_lr * 0.1)
        tr_loss_sum, seen = 0.0, 0
        for imgs, ys, _ids in tqdm(train_loader, desc=f'OrdFold{fold} Ep{ep}/{epochs} train', leave=False):
            imgs = imgs.to(device, non_blocking=True)
            ys = ys.long().to(device, non_blocking=True)
            # build ordinal multi-hot targets: t_k = 1 if y>k
            t = torch.stack([(ys > k).float() for k in range(4)], dim=1)
            opt.zero_grad(set_to_none=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    logits = model(imgs)
                    loss = criterion(logits, t)
                scaler.scale(loss).backward()
                if grad_clip is not None:
                    scaler.unscale_(opt)
                    nn.utils.clip_grad_norm_(model.parameters(), grad_clip)
                scaler.step(opt)
                scaler.update()
            else:
                logits = model(imgs)
                loss = criterion(logits, t)
                loss.backward()
                if grad_clip is not None:
                    nn.utils.clip_grad_norm_(model.parameters(), grad_clip)
                opt.step()
            bs = imgs.size(0)
            tr_loss_sum += loss.item() * bs
            seen += bs
        tr_loss = tr_loss_sum / max(1, seen)
        if ep == 1:
            _set_lr(opt, base_lr)
        else:
            scheduler.step()

        # validate
        model.eval()
        all_scores = []
        with torch.inference_mode():
            for imgs, ys, _ids in tqdm(valid_loader, desc=f'OrdFold{fold} Ep{ep}/{epochs} valid', leave=False):
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        s = model.predict_score(imgs)
                else:
                    s = model.predict_score(imgs)
                all_scores.append(s.detach().float().cpu())
        all_scores = torch.cat(all_scores).numpy().reshape(-1)
        th = optimize_thresholds(all_scores, y_va, init=best_th, n_iter=8)
        preds_lbl = preds_to_labels_reg(all_scores, th)
        qwk = qwk_score(y_va, preds_lbl)
        print(f'[Ordinal] Epoch {ep}: train_loss={tr_loss:.4f} val_qwk={qwk:.4f} th={[round(float(x),4) for x in th]}')

        if qwk > best_qwk + 1e-5:
            best_qwk = qwk
            best_state = {k: v.cpu() for k, v in model.state_dict().items()}
            best_th = th
            bad = 0
            torch.save(best_state, f'model_{model_name}_fold{fold}.pth')
            try:
                np.save(f'thresholds_{model_name}_fold{fold}.npy', np.array(best_th, dtype=np.float32))
            except Exception:
                pass
        else:
            bad += 1
            if bad >= patience:
                print('Early stopping (ordinal).')
                break

    if best_state is not None:
        model.load_state_dict(best_state)
    # final val preds
    val_preds = []
    pw = True if num_workers > 0 else False
    with torch.inference_mode():
        for imgs, ys, _ids in DataLoader(valid_loader.dataset, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False, persistent_workers=pw, worker_init_fn=_seed_worker if num_workers>0 else None):
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    s = model.predict_score(imgs)
            else:
                s = model.predict_score(imgs)
            val_preds.append(s.detach().float().cpu())
    val_preds = torch.cat(val_preds).numpy().reshape(-1)

    del train_loader, valid_loader
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    return {
        'model': model,
        'optimizer': opt,
        'scheduler': scheduler,
        'best_qwk': best_qwk,
        'best_th': best_th,
        'y_va': y_va,
        'val_ids': val_ids,
        'val_preds': val_preds
    }

def infer_test_preds_ordinal(model: nn.Module, test_ids: List[str], batch_size: int = 8, num_workers: int = 0, tta: int = 4) -> np.ndarray:
    device, can_amp = _pick_device(min_free_bytes=2*1024*1024*1024)
    ds = RetinaDataset(test_ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    pw = True if num_workers > 0 else False
    dl = DataLoader(ds, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=False, persistent_workers=pw, worker_init_fn=_seed_worker if num_workers>0 else None)
    model = model.to(device).eval()
    preds = []
    use_amp = can_amp
    if device.type == 'cpu':
        tta = 0
    with torch.inference_mode():
        for batch in tqdm(dl, desc='Test infer (ordinal)', leave=False):
            imgs, id_batch = batch
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    p0 = model.predict_score(imgs)
            else:
                p0 = model.predict_score(imgs)
            if tta and tta >= 4:
                imgs_h = torch.flip(imgs, dims=[3])
                imgs_v = torch.flip(imgs, dims=[2])
                imgs_hv = torch.flip(imgs, dims=[2, 3])
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p_h = model.predict_score(imgs_h)
                        p_v = model.predict_score(imgs_v)
                        p_hv = model.predict_score(imgs_hv)
                else:
                    p_h = model.predict_score(imgs_h)
                    p_v = model.predict_score(imgs_v)
                    p_hv = model.predict_score(imgs_hv)
                p = (p0 + p_h + p_v + p_hv) / 4.0
            else:
                p = p0
            preds.append(p.detach().float().cpu())
    preds = torch.cat(preds).numpy().reshape(-1)
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    return preds

# ----- Orchestrate 5-fold ordinal training at 256px and blend -----
NUM_FOLDS = 5
ORD_EPOCHS = 20
ORD_BS = 4
ORD_LR = 1e-4
ORD_WD = 1e-4
ORD_PATIENCE = 5
ORD_NAME = 'res34_ordinal_256px'

df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()

ord_oof_preds_all, ord_oof_y_all, ord_ids_all = [], [], []
ord_test_preds_accum = None
prev_best_th = None

for fold in range(NUM_FOLDS):
    try:
        res = train_one_fold_ordinal(fold, epochs=ORD_EPOCHS, batch_size=ORD_BS, lr=ORD_LR, wd=ORD_WD, grad_clip=1.0, num_workers=0, patience=ORD_PATIENCE, init_th=prev_best_th, model_name=ORD_NAME, force_amp=None)
    except RuntimeError as e:
        msg = str(e)
        if ('CUDA out of memory' in msg) or ('CUBLAS_STATUS_ALLOC_FAILED' in msg) or ('CUDA error' in msg):
            print(f'[Ordinal] Fold {fold}: CUDA error. Retrying with AMP disabled...')
            if torch.cuda.is_available():
                torch.cuda.empty_cache()
            res = train_one_fold_ordinal(fold, epochs=ORD_EPOCHS, batch_size=ORD_BS, lr=ORD_LR, wd=ORD_WD, grad_clip=1.0, num_workers=0, patience=ORD_PATIENCE, init_th=prev_best_th, model_name=ORD_NAME, force_amp=False)
        else:
            raise
    print(f'[Ordinal] Fold {fold} best QWK: {res["best_qwk"]:.4f}')
    ord_oof_preds_all.append(res['val_preds'])
    ord_oof_y_all.append(res['y_va'])
    ord_ids_all.extend(res['val_ids'])
    prev_best_th = res['best_th']
    fold_test_preds = infer_test_preds_ordinal(res['model'], test_ids, batch_size=8, num_workers=0, tta=4)
    ord_test_preds_accum = fold_test_preds if ord_test_preds_accum is None else (ord_test_preds_accum + fold_test_preds)
    m, o, sch = res['model'], res['optimizer'], res['scheduler']
    del m, o, sch
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    import gc; gc.collect()

ord_oof_preds_all = np.concatenate(ord_oof_preds_all)
ord_oof_y_all = np.concatenate(ord_oof_y_all).astype(int)
ord_test_preds_mean = ord_test_preds_accum / float(NUM_FOLDS)
np.save('oof_preds_ordinal.npy', ord_oof_preds_all)
np.save('oof_y_ordinal.npy', ord_oof_y_all)

# Load regression OOF with ids and align by id_code
df_reg_oof = pd.read_csv('oof_predictions.csv')  # has id_code, oof_pred
df_ord_oof = pd.DataFrame({'id_code': ord_ids_all, 'ord_oof_pred': ord_oof_preds_all, 'y_true': ord_oof_y_all})
df_merged_oof = df_ord_oof.merge(df_reg_oof[['id_code','oof_pred']], on='id_code', how='inner')
assert len(df_merged_oof) == len(df_ord_oof), 'OOF align mismatch after merge.'
reg_oof_aligned = df_merged_oof['oof_pred'].values
ord_oof_aligned = df_merged_oof['ord_oof_pred'].values
y_true_aligned = df_merged_oof['y_true'].values.astype(int)

# Regression test inference with the SAME 4x TTA for consistency
def infer_reg_test_mean_tta(ids: List[str], tta: int = 4) -> np.ndarray:
    device, can_amp = _pick_device(min_free_bytes=2*1024*1024*1024)
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=32, shuffle=False, num_workers=0, pin_memory=False)
    preds_all_folds = []
    use_amp = can_amp
    for fold in range(NUM_FOLDS):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        preds = []
        tta_eff = tta if device.type == 'cuda' else 0
        with torch.inference_mode():
            for batch in dl:
                imgs, idb = batch
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p0 = m(imgs)
                else:
                    p0 = m(imgs)
                if tta_eff and tta_eff >= 4:
                    imgs_h = torch.flip(imgs, dims=[3])
                    imgs_v = torch.flip(imgs, dims=[2])
                    imgs_hv = torch.flip(imgs, dims=[2, 3])
                    if use_amp:
                        with torch.amp.autocast('cuda', enabled=True):
                            p_h = m(imgs_h)
                            p_v = m(imgs_v)
                            p_hv = m(imgs_hv)
                    else:
                        p_h = m(imgs_h)
                        p_v = m(imgs_v)
                        p_hv = m(imgs_hv)
                    p = (p0 + p_h + p_v + p_hv) / 4.0
                else:
                    p = p0
                preds.append(p.detach().float().cpu())
        preds_all_folds.append(torch.cat(preds).numpy().reshape(-1))
        del m, sd
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
    assert len(preds_all_folds) > 0, 'No regression fold checkpoints found.'
    return np.mean(np.vstack(preds_all_folds), axis=0)

reg_test_mean = infer_reg_test_mean_tta(test_ids, tta=4)

# Blend OOF with alignment and re-optimize thresholds globally
blend_oof = 0.5 * reg_oof_aligned + 0.5 * ord_oof_aligned
init_global = list(np.quantile(blend_oof, [0.2, 0.4, 0.6, 0.8]))
best_th = optimize_thresholds(blend_oof, y_true_aligned, init=init_global, n_iter=60)
blend_labels = preds_to_labels_reg(blend_oof, best_th)
blend_qwk = qwk_score(y_true_aligned, blend_labels)
print('Blended OOF QWK:', round(float(blend_qwk), 5), ' thresholds:', [round(float(x),4) for x in best_th])

# Test blend with consistent ordering
df_blend_test = pd.DataFrame({'id_code': test_ids})
df_blend_test['reg_pred'] = reg_test_mean
df_blend_test['ord_pred'] = ord_test_preds_mean
blend_test = 0.5 * df_blend_test['reg_pred'].values + 0.5 * df_blend_test['ord_pred'].values
test_labels = preds_to_labels_reg(blend_test, best_th).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels}).to_csv('submission.csv', index=False)
with open('global_thresholds_blend.json', 'w') as f:
    json.dump({'thresholds': [float(x) for x in best_th], 'oof_qwk': float(blend_qwk), 'model': 'res34_reg+ordinal_256px'}, f, indent=2)
print('submission.csv saved (blend). Rows:', len(test_labels))

Waiting for GPU: free 0.58GB / 15.77GB; need 2.00GB. Retrying in 10s...


Waiting for GPU: free 0.58GB / 15.77GB; need 2.00GB. Retrying in 10s...


Waiting for GPU: free 0.58GB / 15.77GB; need 2.00GB. Retrying in 10s...


Waiting for GPU: free 0.58GB / 15.77GB; need 2.00GB. Retrying in 10s...


Waiting for GPU: free 0.11GB / 15.77GB; need 2.00GB. Retrying in 10s...


...

OrdFold0 Ep1/20 train:   1%|          | 7/659 [00:39<54:15,  4.99s/it]

OrdFold0 Ep1/20 train:   1%|          | 8/659 [00:44<53:34,  4.94s/it]

OrdFold0 Ep1/20 train:   1%|▏         | 9/659 [00:48<52:46,  4.87s/it]

OrdFold0 Ep1/20 train:   2%|▏         | 10/659 [00:53<51:39,  4.78s/it]

OrdFold0 Ep1/20 train:   2%|▏         | 11/659 [00:58<51:35,  4.78s/it]

In [13]:
# Ordinal inference-only from existing checkpoints + aligned blend with regression (grid-search weights) + submission
import json, numpy as np, pandas as pd, torch
import torch.nn as nn
from torch.utils.data import DataLoader
from pathlib import Path
from typing import List

assert FOLDS_CSV.exists(), 'folds_seed42_k5.csv missing.'
df_folds = pd.read_csv(FOLDS_CSV)
NUM_FOLDS = 5

def _extract_state_dict(obj):
    if isinstance(obj, dict):
        if 'state_dict' in obj and isinstance(obj['state_dict'], dict):
            return obj['state_dict']
    return obj

def _adapt_tv_resnet34_keys(state_dict: dict) -> dict:
    # Map torchvision downsample naming differences: '.downsample.conv'->'.downsample.0', '.downsample.bn'->'.downsample.1'
    from collections import OrderedDict
    new_sd = OrderedDict()
    for k, v in state_dict.items():
        nk = k
        if '.downsample.conv.' in nk:
            nk = nk.replace('.downsample.conv.', '.downsample.0.')
        if '.downsample.bn.' in nk:
            nk = nk.replace('.downsample.bn.', '.downsample.1.')
        new_sd[nk] = v
    return new_sd

def _infer_ordinal_val_fold(fold: int, bs: int = 8) -> tuple[np.ndarray, np.ndarray, list[str]]:
    # Build val loader
    val = df_folds[df_folds['fold'] == fold].reset_index(drop=True)
    val_ids = val['id_code'].tolist()
    y_va = val['diagnosis'].values.astype(int)
    ds = RetinaDataset(val_ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, labels=y_va, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    # Load model
    ckpt = Path(f'model_ResNet34Ordinal_fold{fold}_best_qwk.pth')
    assert ckpt.exists(), f'Missing checkpoint {ckpt}'
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    model = ResNet34Ordinal(dropout=0.2).to(device).eval()
    sd = torch.load(ckpt, map_location='cpu')
    sd = _extract_state_dict(sd)
    sd = _adapt_tv_resnet34_keys(sd)
    model.load_state_dict(sd, strict=False)
    preds = []
    use_amp = torch.cuda.is_available()
    with torch.inference_mode():
        for imgs, ys, ids_b in dl:
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    s = model.predict_score(imgs)
            else:
                s = model.predict_score(imgs)
            preds.append(s.detach().float().cpu())
    preds = torch.cat(preds).numpy().reshape(-1)
    return preds, y_va, val_ids

def _infer_ordinal_test_mean_tta(ids: List[str], bs: int = 16, tta: int = 4) -> np.ndarray:
    # Average predictions over folds with 4x flip TTA
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    out_folds = []
    for fold in range(NUM_FOLDS):
        ckpt = Path(f'model_ResNet34Ordinal_fold{fold}_best_qwk.pth')
        if not ckpt.exists():
            continue
        model = ResNet34Ordinal(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        sd = _extract_state_dict(sd)
        sd = _adapt_tv_resnet34_keys(sd)
        model.load_state_dict(sd, strict=False)
        preds = []
        use_amp = torch.cuda.is_available()
        tta_eff = tta if device.type == 'cuda' else 0
        with torch.inference_mode():
            for batch in dl:
                imgs, idb = batch
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p0 = model.predict_score(imgs)
                else:
                    p0 = model.predict_score(imgs)
                if tta_eff and tta_eff >= 4:
                    imgs_h = torch.flip(imgs, dims=[3])
                    imgs_v = torch.flip(imgs, dims=[2])
                    imgs_hv = torch.flip(imgs, dims=[2, 3])
                    if use_amp:
                        with torch.amp.autocast('cuda', enabled=True):
                            p_h = model.predict_score(imgs_h)
                            p_v = model.predict_score(imgs_v)
                            p_hv = model.predict_score(imgs_hv)
                    else:
                        p_h = model.predict_score(imgs_h)
                        p_v = model.predict_score(imgs_v)
                        p_hv = model.predict_score(imgs_hv)
                    p = (p0 + p_h + p_v + p_hv) / 4.0
                else:
                    p = p0
                preds.append(p.detach().float().cpu())
        out_folds.append(torch.cat(preds).numpy().reshape(-1))
        del model, sd
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
    assert len(out_folds) > 0, 'No ordinal fold checkpoints found.'
    return np.mean(np.vstack(out_folds), axis=0)

# Build ordinal OOF
ord_oof_preds_all, ord_oof_y_all, ord_ids_all = [], [], []
for f in range(NUM_FOLDS):
    p, y, ids = _infer_ordinal_val_fold(f, bs=16)
    ord_oof_preds_all.append(p)
    ord_oof_y_all.append(y)
    ord_ids_all.extend(ids)
ord_oof_preds_all = np.concatenate(ord_oof_preds_all)
ord_oof_y_all = np.concatenate(ord_oof_y_all).astype(int)
pd.DataFrame({'id_code': ord_ids_all, 'ord_oof_pred': ord_oof_preds_all, 'y_true': ord_oof_y_all}).to_csv('oof_predictions_ordinal.csv', index=False)

# Load regression OOF and align by id_code
df_reg_oof = pd.read_csv('oof_predictions.csv')  # id_code, oof_pred
df_ord_oof = pd.DataFrame({'id_code': ord_ids_all, 'ord_oof_pred': ord_oof_preds_all, 'y_true': ord_oof_y_all})
df_merged = df_ord_oof.merge(df_reg_oof[['id_code','oof_pred']], on='id_code', how='inner')
assert len(df_merged) == len(df_ord_oof), 'OOF align mismatch.'
reg_oof = df_merged['oof_pred'].values
ord_oof = df_merged['ord_oof_pred'].values
y_true = df_merged['y_true'].values.astype(int)

# Regression test preds with 4x TTA over folds
def infer_reg_test_mean_tta(ids: List[str], tta: int = 4) -> np.ndarray:
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=32, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    out = []
    for fold in range(NUM_FOLDS):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        preds = []
        use_amp = torch.cuda.is_available()
        tta_eff = tta if device.type == 'cuda' else 0
        with torch.inference_mode():
            for batch in dl:
                imgs, idb = batch
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p0 = m(imgs)
                else:
                    p0 = m(imgs)
                if tta_eff and tta_eff >= 4:
                    imgs_h = torch.flip(imgs, dims=[3])
                    imgs_v = torch.flip(imgs, dims=[2])
                    imgs_hv = torch.flip(imgs, dims=[2, 3])
                    if use_amp:
                        with torch.amp.autocast('cuda', enabled=True):
                            p_h = m(imgs_h)
                            p_v = m(imgs_v)
                            p_hv = m(imgs_hv)
                    else:
                        p_h = m(imgs_h)
                        p_v = m(imgs_v)
                        p_hv = m(imgs_hv)
                    p = (p0 + p_h + p_v + p_hv) / 4.0
                else:
                    p = p0
                preds.append(p.detach().float().cpu())
        out.append(torch.cat(preds).numpy().reshape(-1))
        del m, sd
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
    assert len(out) == NUM_FOLDS, 'Missing some regression fold checkpoints.'
    return np.mean(np.vstack(out), axis=0)

# Build test ids
df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()
ord_test_mean = _infer_ordinal_test_mean_tta(test_ids, bs=32, tta=4)
reg_test_mean = infer_reg_test_mean_tta(test_ids, tta=4)

# Grid-search blend weight and re-optimize thresholds on OOF
best_w, best_q, best_th = None, -1.0, None
weights = [round(w, 2) for w in np.arange(0.30, 0.71, 0.05)]
for w in weights:
    blend = w * reg_oof + (1.0 - w) * ord_oof
    init_th = list(np.quantile(blend, [0.2, 0.4, 0.6, 0.8]))
    th = optimize_thresholds(blend, y_true, init=init_th, n_iter=60)
    labels = preds_to_labels_reg(blend, th)
    q = qwk_score(y_true, labels)
    if q > best_q:
        best_q, best_w, best_th = q, w, th
print('Best blend OOF:', round(float(best_q),5), ' at w(reg)=', best_w, ' thresholds=', [round(float(x),4) for x in best_th])

# Apply to test and save submission
blend_test = best_w * reg_test_mean + (1.0 - best_w) * ord_test_mean
test_labels = preds_to_labels_reg(blend_test, best_th).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels}).to_csv('submission.csv', index=False)
with open('global_thresholds_blend.json', 'w') as f:
    json.dump({'thresholds': [float(x) for x in best_th], 'oof_qwk': float(best_q), 'w_reg': float(best_w), 'note': 'reg+ordinal 256px TTA4'}, f, indent=2)
print('submission.csv saved. Rows:', len(test_labels), ' OOF_QWK:', round(float(best_q),5), ' w_reg=', best_w)

/tmp/ipykernel_2492/245151004.py:43: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


/tmp/ipykernel_2492/245151004.py:72: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


/tmp/ipykernel_2492/245151004.py:143: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


Best blend OOF: 0.85414  at w(reg)= 0.7  thresholds= [0.7302, 0.9965, 1.8694, 2.7373]
submission.csv saved. Rows: 367  OOF_QWK: 0.85414  w_reg= 0.7


In [15]:
# Inference-only: 384px center-crop using existing ResNet34 regression checkpoints (no training)
import numpy as np, pandas as pd, torch
import torch.nn as nn
from torch.utils.data import DataLoader
from pathlib import Path
from typing import List

# Switch globals to 384px cache/size for inference
IMG_SIZE = 384
TARGET_SIZE = IMG_SIZE
CACHE_DIR = DATA_DIR / 'cache_384_retina_v1'
CACHE_TRAIN_DIR = CACHE_DIR / 'train_416'
CACHE_TEST_DIR  = CACHE_DIR / 'test_416'
CACHE_SIZE = 416
print('Switched to 384px inference. CACHE_DIR:', str(CACHE_DIR))

assert FOLDS_CSV.exists(), 'Missing folds file'
df_folds = pd.read_csv(FOLDS_CSV)

def _infer_val_fold_384(fold: int, bs: int = 16) -> tuple[np.ndarray, np.ndarray, list[str]]:
    val = df_folds[df_folds['fold'] == fold].reset_index(drop=True)
    ids = val['id_code'].tolist()
    y = val['diagnosis'].values.astype(int)
    ds = RetinaDataset(ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, labels=y, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    m = ResNet34Regressor(dropout=0.2).to(device).eval()
    ckpt = Path(f'model_res34_256px_fold{fold}.pth')
    assert ckpt.exists(), f'Missing {ckpt}'
    sd = torch.load(ckpt, map_location='cpu')
    m.load_state_dict(sd, strict=True)
    preds = []
    use_amp = torch.cuda.is_available()
    with torch.inference_mode():
        for imgs, ys, _ids in dl:
            imgs = imgs.to(device, non_blocking=True)
            if use_amp:
                with torch.amp.autocast('cuda', enabled=True):
                    p = m(imgs)
            else:
                p = m(imgs)
            preds.append(p.detach().float().cpu())
    preds = torch.cat(preds).numpy().reshape(-1)
    return preds, y, ids

def _infer_test_384_mean_tta(ids: List[str], bs: int = 32, tta: int = 4) -> np.ndarray:
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_valid_transforms())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    out = []
    for fold in range(5):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        preds = []
        use_amp = torch.cuda.is_available()
        tta_eff = tta if device.type == 'cuda' else 0
        with torch.inference_mode():
            for batch in dl:
                imgs, idb = batch
                imgs = imgs.to(device, non_blocking=True)
                if use_amp:
                    with torch.amp.autocast('cuda', enabled=True):
                        p0 = m(imgs)
                else:
                    p0 = m(imgs)
                if tta_eff and tta_eff >= 4:
                    imgs_h = torch.flip(imgs, dims=[3])
                    imgs_v = torch.flip(imgs, dims=[2])
                    imgs_hv = torch.flip(imgs, dims=[2, 3])
                    if use_amp:
                        with torch.amp.autocast('cuda', enabled=True):
                            p_h = m(imgs_h)
                            p_v = m(imgs_v)
                            p_hv = m(imgs_hv)
                    else:
                        p_h = m(imgs_h)
                        p_v = m(imgs_v)
                        p_hv = m(imgs_hv)
                    p = (p0 + p_h + p_v + p_hv) / 4.0
                else:
                    p = p0
                preds.append(p.detach().float().cpu())
        out.append(torch.cat(preds).numpy().reshape(-1))
        del m, sd
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
    assert len(out) > 0, 'No regression fold checkpoints found.'
    return np.mean(np.vstack(out), axis=0)

# Build 384px OOF preds
oof_preds_384, oof_y_384, oof_ids_384 = [], [], []
for f in range(5):
    p, y, ids = _infer_val_fold_384(f, bs=16)
    oof_preds_384.append(p); oof_y_384.append(y); oof_ids_384.extend(ids)
oof_preds_384 = np.concatenate(oof_preds_384)
oof_y_384 = np.concatenate(oof_y_384).astype(int)
pd.DataFrame({'id_code': oof_ids_384, 'oof_pred_384': oof_preds_384, 'y_true': oof_y_384}).to_csv('oof_predictions_384.csv', index=False)

# Optimize thresholds on 384 OOF and infer test at 384
th_384 = optimize_thresholds(oof_preds_384, oof_y_384, init=list(np.quantile(oof_preds_384, [0.2,0.4,0.6,0.8])), n_iter=60)
qwk_384 = qwk_score(oof_y_384, preds_to_labels_reg(oof_preds_384, th_384))
print('OOF QWK @384-infer:', round(float(qwk_384),5), ' th:', [round(float(x),4) for x in th_384])

df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()
test_preds_384 = _infer_test_384_mean_tta(test_ids, bs=32, tta=4)
test_labels_384 = preds_to_labels_reg(test_preds_384, th_384).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels_384}).to_csv('submission.csv', index=False)
with open('global_thresholds_384.json', 'w') as f:
    import json; json.dump({'thresholds': [float(x) for x in th_384], 'oof_qwk': float(qwk_384), 'note': '384px infer only from 256px model'}, f, indent=2)
print('submission.csv saved (384-infer). Rows:', len(test_labels_384), ' OOF_QWK_384:', round(float(qwk_384),5))

Switched to 384px inference. CACHE_DIR: /app/agent_run_states/aptos2019-blindness-detection/cache_384_retina_v1


/tmp/ipykernel_2492/2342144633.py:30: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


OOF QWK @384-infer: 0.84259  th: [0.8135, 1.1178, 2.142, 3.1325]


/tmp/ipykernel_2492/2342144633.py:56: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


In [18]:
# 256px ResNet34 inference with OOF-validated TTA (8x fallback to 4x) + threshold re-optimization + submission
import json, numpy as np, pandas as pd, torch
import torch.nn as nn
from torch.utils.data import DataLoader
from pathlib import Path

# Ensure we are on 256px cache/paths
IMG_SIZE = 256
TARGET_SIZE = IMG_SIZE
CACHE_DIR = DATA_DIR / 'cache_256_retina_v1'
CACHE_TRAIN_DIR = CACHE_DIR / 'train_288'
CACHE_TEST_DIR  = CACHE_DIR / 'test_288'
CACHE_SIZE = 288
print('Using 256px config for TTA. CACHE_DIR:', str(CACHE_DIR))

assert FOLDS_CSV.exists(), 'Missing folds file'
df_folds = pd.read_csv(FOLDS_CSV)

# Inference transform: NORMALIZE ONLY (no crop). We will apply geom TTA first, then center-crop on tensor to match training.
def get_infer_transforms_no_crop():
    return Compose([Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD, max_pixel_value=255.0)])

def _center_crop_tensor(x: torch.Tensor, size: int) -> torch.Tensor:
    # x: [B,3,H,W] -> center crop to [B,3,size,size]
    B, C, H, W = x.shape
    if H == size and W == size:
        return x
    top = max(0, (H - size) // 2)
    left = max(0, (W - size) // 2)
    return x[:, :, top:top+size, left:left+size]

def _tta_apply(imgs: torch.Tensor, mode: str, model: nn.Module, use_amp: bool) -> torch.Tensor:
    # imgs: [B,3,H,W] normalized, uncropped; apply TTA -> center-crop -> predict; returns [B]
    def _forward(x):
        x = _center_crop_tensor(x, TARGET_SIZE)
        if use_amp and torch.cuda.is_available():
            with torch.amp.autocast('cuda', enabled=True):
                return model(x)
        else:
            return model(x)
    preds_accum = None
    count = 0
    if mode == '8x':
        for k in (0,1,2,3):
            x = torch.rot90(imgs, k=k, dims=(2,3))
            p0 = _forward(x)  # [B]
            xh = torch.flip(x, dims=[3])
            ph = _forward(xh)  # [B]
            preds_accum = (p0 + ph) if preds_accum is None else (preds_accum + p0 + ph)
            count += 2
    elif mode == '4x':
        variants = [imgs, torch.flip(imgs, dims=[3]), torch.flip(imgs, dims=[2]), torch.flip(imgs, dims=[2,3])]
        for x in variants:
            p = _forward(x)  # [B]
            preds_accum = p if preds_accum is None else (preds_accum + p)
            count += 1
    elif mode == '2x':
        variants = [imgs, torch.flip(imgs, dims=[3])]
        for x in variants:
            p = _forward(x)
            preds_accum = p if preds_accum is None else (preds_accum + p)
            count += 1
    else:
        p = _forward(imgs)  # [B]
        return p.detach().float().cpu().view(-1)
    out = (preds_accum / float(count)).detach().float().cpu().view(-1)
    return out

def infer_val_fold_tta(fold: int, bs: int, mode: str) -> tuple[np.ndarray, np.ndarray, list[str]]:
    val = df_folds[df_folds['fold'] == fold].reset_index(drop=True)
    ids = val['id_code'].tolist()
    y = val['diagnosis'].values.astype(int)
    ds = RetinaDataset(ids, TRAIN_IMG_DIR, CACHE_TRAIN_DIR, labels=y, transform=get_infer_transforms_no_crop())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    m = ResNet34Regressor(dropout=0.2).to(device).eval()
    ckpt = Path(f'model_res34_256px_fold{fold}.pth')
    assert ckpt.exists(), f'Missing {ckpt}'
    sd = torch.load(ckpt, map_location='cpu')
    m.load_state_dict(sd, strict=True)
    preds = []
    use_amp = torch.cuda.is_available()
    with torch.inference_mode():
        for imgs, ys, _ids in dl:
            imgs = imgs.to(device, non_blocking=True)
            p = _tta_apply(imgs, mode, m, use_amp)  # [B]
            preds.append(p)
    preds = torch.cat(preds).numpy().reshape(-1)
    return preds, y, ids

def infer_test_mean_tta(ids: list[str], bs: int, mode: str) -> np.ndarray:
    ds = RetinaDataset(ids, TEST_IMG_DIR, CACHE_TEST_DIR, labels=None, transform=get_infer_transforms_no_crop())
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    use_amp = torch.cuda.is_available()
    fold_outs = []
    for fold in range(5):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        preds = []
        with torch.inference_mode():
            for imgs, idb in dl:
                imgs = imgs.to(device, non_blocking=True)
                p = _tta_apply(imgs, mode, m, use_amp)  # [B]
                preds.append(p)
        fold_outs.append(torch.cat(preds).numpy().reshape(-1))
        del m, sd
        if torch.cuda.is_available():
            torch.cuda.empty_cache()
    assert len(fold_outs) > 0, 'No fold checkpoints found.'
    return np.mean(np.vstack(fold_outs), axis=0)

def _enforce_monotonic(th):
    th = list(th)
    th[1] = max(th[1], th[0] + 1e-4)
    th[2] = max(th[2], th[1] + 1e-4)
    th[3] = max(th[3], th[2] + 1e-4)
    return th

def qwk_score_np(y_true: np.ndarray, y_pred: np.ndarray, n_classes: int = 5) -> float:
    y_true = y_true.astype(int).ravel()
    y_pred = y_pred.astype(int).ravel()
    O = np.zeros((n_classes, n_classes), dtype=np.float64)
    for t, p in zip(y_true, y_pred):
        if 0 <= t < n_classes and 0 <= p < n_classes:
            O[t, p] += 1
    N = O.sum()
    if N == 0:
        return 0.0
    hist_true = O.sum(axis=1)
    hist_pred = O.sum(axis=0)
    E = np.outer(hist_true, hist_pred) / (N + 1e-12)
    W = np.zeros((n_classes, n_classes), dtype=np.float64)
    for i in range(n_classes):
        for j in range(n_classes):
            W[i, j] = ((i - j) ** 2) / ((n_classes - 1) ** 2)
    num = (W * O).sum()
    den = (W * E).sum() + 1e-12
    return 1.0 - num / den

def preds_to_labels_reg_np(preds: np.ndarray, th):
    t0, t1, t2, t3 = th
    return np.digitize(preds, bins=[t0, t1, t2, t3]).astype(int)

# Load baseline OOF artifacts/thresholds
oof_preds_base = np.load('oof_preds.npy') if Path('oof_preds.npy').exists() else None
oof_y_base = np.load('oof_y.npy').astype(int) if Path('oof_y.npy').exists() else None
assert oof_preds_base is not None and oof_y_base is not None, 'Missing baseline OOF artifacts.'
try:
    with open('global_thresholds_scipy.json','r') as f:
        base = json.load(f)
        base_th = base.get('thresholds', None)
        base_q = float(base.get('oof_qwk', -1.0))
except Exception:
    base_th, base_q = None, -1.0
if base_th is None or len(base_th) != 4:
    init = list(np.quantile(oof_preds_base, [0.2,0.4,0.6,0.8]))
    base_th = _enforce_monotonic(init)
    base_q = qwk_score_np(oof_y_base, preds_to_labels_reg_np(oof_preds_base, base_th))
print('Baseline OOF QWK:', round(base_q,5))

# Step 1–3: 8x TTA OOF + thresholds (geom before crop) — if not better, try 4x, then 2x H-flip
modes_to_try = ['8x', '4x', '2x']
best_mode, best_th, best_q = None, base_th, base_q
oof_cache = {}
for tta_mode in modes_to_try:
    oof_preds_tta, oof_y_tta, oof_ids_tta = [], [], []
    for f in range(5):
        p, y, ids = infer_val_fold_tta(f, bs=32, mode=tta_mode)
        oof_preds_tta.append(p); oof_y_tta.append(y); oof_ids_tta.extend(ids)
    oof_preds_tta = np.concatenate(oof_preds_tta)
    oof_y_tta = np.concatenate(oof_y_tta).astype(int)
    init_th = list(np.quantile(oof_preds_tta, [0.2,0.4,0.6,0.8]))
    th = _enforce_monotonic(init_th)
    th = optimize_thresholds(oof_preds_tta, oof_y_tta, init=th, n_iter=60)
    q = qwk_score_np(oof_y_tta, preds_to_labels_reg_np(oof_preds_tta, th))
    print(f'OOF QWK {tta_mode} (opt):', round(q,5), ' th:', [round(float(x),4) for x in th])
    oof_cache[tta_mode] = (oof_ids_tta, oof_preds_tta, oof_y_tta, th, q)
    if q > best_q + 1e-5:
        best_mode, best_th, best_q = tta_mode, th, q

print('Chosen mode:', best_mode if best_mode is not None else 'no-TTA (revert baseline)')
print('Chosen OOF QWK:', round(best_q,5))

# Step 5–6: Test inference with chosen mode (or revert to baseline no-TTA)
df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()
mode_to_use = best_mode if best_mode is not None else 'none'
test_mean = infer_test_mean_tta(test_ids, bs=32, mode=mode_to_use)
test_labels = preds_to_labels_reg_np(test_mean, best_th).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels}).to_csv('submission.csv', index=False)
with open('global_thresholds_tta.json','w') as f:
    json.dump({'mode': mode_to_use, 'thresholds': [float(x) for x in best_th], 'oof_qwk': float(best_q)}, f, indent=2)
print('submission.csv saved. Test rows:', len(test_labels))

# Save OOF TTA artifacts for audit
if best_mode in oof_cache:
    ids, preds, ys, th, q = oof_cache[best_mode]
    pd.DataFrame({'id_code': ids, f'oof_pred_tta_{best_mode}': preds, 'y_true': ys}).to_csv(f'oof_predictions_tta_{best_mode}.csv', index=False)

Using 256px config for TTA. CACHE_DIR: /app/agent_run_states/aptos2019-blindness-detection/cache_256_retina_v1
Baseline OOF QWK: 0.86381


/tmp/ipykernel_2492/603875550.py:79: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


OOF QWK 8x (opt): 0.85588  th: [0.8945, 1.2768, 2.5885, 3.8934]


OOF QWK 4x (opt): 0.84933  th: [0.7871, 1.2058, 2.5235, 3.7207]


OOF QWK 2x (opt): 0.84909  th: [0.74, 1.2832, 2.3527, 3.856]
Chosen mode: no-TTA (revert baseline)
Chosen OOF QWK: 0.86381


/tmp/ipykernel_2492/603875550.py:102: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


submission.csv saved. Test rows: 367


In [20]:
# Resolution blending (256px + 384px) with center-crop only, re-optimized thresholds, final submission
import json, numpy as np, pandas as pd, torch
import torch.nn as nn
from torch.utils.data import DataLoader
from pathlib import Path

assert FOLDS_CSV.exists(), 'Missing folds file'
df_folds = pd.read_csv(FOLDS_CSV)

# --- Size-specific valid transform (center-crop) ---
def get_valid_transforms_for(size: int):
    return Compose([CenterCrop(size, size), Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD, max_pixel_value=255.0)])

# --- Helpers: test inference (center-crop only; no TTA), explicit crop size ---
def _infer_test_mean_center(ids, cache_dir, crop_size: int, bs=32):
    ds = RetinaDataset(ids, TEST_IMG_DIR, cache_dir, labels=None, transform=get_valid_transforms_for(crop_size))
    dl = DataLoader(ds, batch_size=bs, shuffle=False, num_workers=0, pin_memory=False)
    # Force CPU to avoid CUDA allocator internal assert at high-res inference
    device = torch.device('cpu')
    fold_outs = []
    for fold in range(5):
        ckpt = Path(f'model_res34_256px_fold{fold}.pth')
        if not ckpt.exists():
            continue
        m = ResNet34Regressor(dropout=0.2).to(device).eval()
        sd = torch.load(ckpt, map_location='cpu')
        m.load_state_dict(sd, strict=True)
        preds = []
        with torch.inference_mode():
            for imgs, idb in dl:
                imgs = imgs.to(device, non_blocking=True)
                p = m(imgs)
                preds.append(p.detach().float().cpu())
        fold_outs.append(torch.cat(preds).numpy().reshape(-1))
        del m, sd
    assert len(fold_outs) > 0, 'No fold checkpoints found.'
    return np.mean(np.vstack(fold_outs), axis=0)

# --- Load/align OOF 256 and 384 ---
df_256 = pd.read_csv('oof_predictions.csv')  # id_code, oof_pred, oof_label
df_384 = pd.read_csv('oof_predictions_384.csv')  # id_code, oof_pred_384, y_true
dfm = df_256.merge(df_384[['id_code','oof_pred_384','y_true']], on='id_code', how='inner')
assert len(dfm) == len(df_384), 'OOF align mismatch (256 vs 384)'
pred_256 = dfm['oof_pred'].values
pred_384 = dfm['oof_pred_384'].values
y_true = dfm['y_true'].values.astype(int)

# --- Blend grid search with threshold re-optimization ---
def _enforce_monotonic(th):
    th = list(th)
    th[1] = max(th[1], th[0] + 1e-4)
    th[2] = max(th[2], th[1] + 1e-4)
    th[3] = max(th[3], th[2] + 1e-4)
    return th

def preds_to_labels_reg_np(preds: np.ndarray, th):
    t0, t1, t2, t3 = th
    return np.digitize(preds, bins=[t0, t1, t2, t3]).astype(int)

def qwk_score_np(y_true: np.ndarray, y_pred: np.ndarray, n_classes: int = 5) -> float:
    y_true = y_true.astype(int).ravel()
    y_pred = y_pred.astype(int).ravel()
    O = np.zeros((n_classes, n_classes), dtype=np.float64)
    for t, p in zip(y_true, y_pred):
        if 0 <= t < n_classes and 0 <= p < n_classes:
            O[t, p] += 1
    N = O.sum()
    if N == 0:
        return 0.0
    hist_true = O.sum(axis=1)
    hist_pred = O.sum(axis=0)
    E = np.outer(hist_true, hist_pred) / (N + 1e-12)
    W = np.zeros((n_classes, n_classes), dtype=np.float64)
    for i in range(n_classes):
        for j in range(n_classes):
            W[i, j] = ((i - j) ** 2) / ((n_classes - 1) ** 2)
    num = (W * O).sum()
    den = (W * E).sum() + 1e-12
    return 1.0 - num / den

def optimize_thresholds_simple(preds: np.ndarray, y_true: np.ndarray, init=None, n_iter: int = 60):
    if init is None:
        init = list(np.quantile(preds, [0.2,0.4,0.6,0.8]))
    th = _enforce_monotonic(init)
    best = qwk_score_np(y_true, preds_to_labels_reg_np(preds, th))
    delta = preds.std() * 0.5 + 1e-6
    for _ in range(n_iter):
        improved = False
        for k in range(4):
            for s in (+1, -1):
                cand = th.copy()
                cand[k] += s * delta
                cand = _enforce_monotonic(cand)
                q = qwk_score_np(y_true, preds_to_labels_reg_np(preds, cand))
                if q > best + 1e-6:
                    th, best, improved = cand, q, True
        delta *= 0.5
        if not improved:
            continue
    return th, best

weights = [round(w, 2) for w in np.arange(0.0, 1.01, 0.05)]
best_w, best_q, best_th = None, -1.0, None
for w in weights:
    blend = w * pred_256 + (1.0 - w) * pred_384
    th0 = list(np.quantile(blend, [0.2,0.4,0.6,0.8]))
    th, q = optimize_thresholds_simple(blend, y_true, init=th0, n_iter=60)
    if q > best_q:
        best_q, best_w, best_th = q, w, th
print('Best OOF blend (256 vs 384):', round(float(best_q),5), ' w_256=', best_w, ' th=', [round(float(x),4) for x in best_th])

# --- Build consistent test preds (center-crop only) for 256 and 384 ---
# 256 cache/size
CACHE_DIR_256 = DATA_DIR / 'cache_256_retina_v1'
CACHE_TEST_DIR_256 = CACHE_DIR_256 / 'test_288'
# 384 cache/size
CACHE_DIR_384 = DATA_DIR / 'cache_384_retina_v1'
CACHE_TEST_DIR_384 = CACHE_DIR_384 / 'test_416'
CACHE_SIZE = 416  # safeguard: ensure 384 cache ops use correct size if caching occurs

df_te = pd.read_csv(TEST_CSV)
test_ids = df_te['id_code'].tolist()

test_pred_256 = _infer_test_mean_center(test_ids, CACHE_TEST_DIR_256, crop_size=256, bs=32)
test_pred_384 = _infer_test_mean_center(test_ids, CACHE_TEST_DIR_384, crop_size=384, bs=32)
blend_test = best_w * test_pred_256 + (1.0 - best_w) * test_pred_384
test_labels = preds_to_labels_reg_np(blend_test, best_th).astype(int)
pd.DataFrame({'id_code': test_ids, 'diagnosis': test_labels}).to_csv('submission.csv', index=False)
with open('global_thresholds_blend_res.json','w') as f:
    json.dump({'strategy': 'res_blend_center', 'w_256': float(best_w), 'thresholds': [float(x) for x in best_th], 'oof_qwk': float(best_q)}, f, indent=2)
print('submission.csv saved (resolution blend). Rows:', len(test_labels))

Best OOF blend (256 vs 384): 0.86471  w_256= 0.7  th= [0.724, 1.2528, 2.4581, 3.4492]


/tmp/ipykernel_2492/2270699997.py:25: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sd = torch.load(ckpt, map_location='cpu')


RuntimeError: !block->expandable_segment_ INTERNAL ASSERT FAILED at "../c10/cuda/CUDACachingAllocator.cpp":2586, please report a bug to PyTorch. 